# 20/11/2022
Update: after finishing cleaning the data, i've decided to split up the notebooks. this way, i will have one notebook cleaning data, one notebook testing machine learning models, and one notebook predicting the world cup. I feel this will be cleaner and more organized and will allow me to navigate with ease

# 17/11/2022
found a new dataset which seems alot more promising than earlier ones. this is because this dataset is up to date and includes player info, match info, team info, etc.

I'm going to explore it to see how it is.

https://github.com/davidcamilo0710/QATAR_2022_Prediction

In [113]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split
from sklearn import metrics
pd.set_option("display.max_columns", None)

# Data files
1. international_matches.csv - This dataset provides a complete overview of all international soccer matches played since the 90s. On top of that, the strength of each team is provided by incorporating actual FIFA rankings as well as player strengths based on the EA Sport FIFA video game.
2. last_team_scores.csv - contains the names of the teams facing each other, the FIFA ranking of each team, and the rating of both teams' defense, midfield, and offense.
3. players_22.csv - The datasets provided include the player data for FIFA 22 Career Mode.
4. Qatar_group_stage.csv
5. squad_stats.csv
6. training.csv - training matches between world cup teams

In [114]:
int_mat = pd.read_csv(r'C:\Users\Lorand\Documents\School\A level\EPQ\Project Itself\Data\2022 data\international_matches.csv')
last_scores = pd.read_csv(r'C:\Users\Lorand\Documents\School\A level\EPQ\Project Itself\Data\2022 data\last_team_scores.csv')
players_22 = pd.read_csv(r'C:\Users\Lorand\Documents\School\A level\EPQ\Project Itself\Data\2022 data\players_22.csv')
gr_st = pd.read_csv(r'C:\Users\Lorand\Documents\School\A level\EPQ\Project Itself\Data\2022 data\Qatar_group_stage.csv')
sq_stats = pd.read_csv(r'C:\Users\Lorand\Documents\School\A level\EPQ\Project Itself\Data\2022 data\squad_stats.csv')
training = pd.read_csv(r'C:\Users\Lorand\Documents\School\A level\EPQ\Project Itself\Data\2022 data\training.csv')
#loaded all datasets

C:\Users\Lorand\AppData\Local\Temp\ipykernel_8376\47462419.py:3: DtypeWarning: Columns (25,108) have mixed types. Specify dtype option on import or set low_memory=False.
  players_22 = pd.read_csv(r'C:\Users\Lorand\Documents\School\A level\EPQ\Project Itself\Data\2022 data\players_22.csv')


# Data exploration
time to explore each file and see what needs to be cleaned


## int_mat (international matches) exploration

In [115]:
int_mat

date       home_team     away_team home_team_continent  \
0      1993-08-08         Bolivia       Uruguay       South America   
1      1993-08-08          Brazil        Mexico       South America   
2      1993-08-08         Ecuador     Venezuela       South America   
3      1993-08-08          Guinea  Sierra Leone              Africa   
4      1993-08-08        Paraguay     Argentina       South America   
...           ...             ...           ...                 ...   
23916  2022-06-14         Moldova       Andorra              Europe   
23917  2022-06-14   Liechtenstein        Latvia              Europe   
23918  2022-06-14           Chile         Ghana       South America   
23919  2022-06-14           Japan       Tunisia                Asia   
23920  2022-06-14  Korea Republic         Egypt                Asia   

      away_team_continent  home_team_fifa_rank  away_team_fifa_rank  \
0           South America                   59                   22   
1           North America                    8                   14   
2           South America                   35                   94   
3                  Africa                   65                   86   
4           South America                   67                    5   
...                   ...                  ...                  ...   
23916              Europe                  180                  153   
23917              Europe                  192                  135   
23918              Africa                   28                   60   
23919              Africa                   23                   35   
23920              Africa                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  away_team_score                    tournament  \
0                    3                1  FIFA World Cup qualification   
1                    1                1                      Friendly   
2                    5                0  FIFA World Cup qualification   
3                    1                0                      Friendly   
4                    1                3  FIFA World Cup qualification   
...                ...              ...                           ...   
23916                2                1           UEFA Nations League   
23917                0                2           UEFA Nations League   
23918                0                0                     Kirin Cup   
23919                0                3                     Kirin Cup   
23920                4                1                      Friendly   

           city         country  neutral_location shoot_out home_team_result  \
0        La Paz         Bolivia             False        No              Win   
1        Maceió          Brazil             False        No             Draw   
2         Quito         Ecuador             False        No              Win   
3       Conakry          Guinea             False        No              Win   
4      Asunción        Paraguay             False        No             Lose   
...         ...             ...               ...       ...              ...   
23916  Chișinău         Moldova             False        No      

In [116]:
int_mat.isna().sum()

date                                 0
home_team                            0
away_team                            0
home_team_continent                  0
away_team_continent                  0
home_team_fifa_rank                  0
away_team_fifa_rank                  0
home_team_total_fifa_points          0
away_team_total_fifa_points          0
home_team_score                      0
away_team_score                      0
tournament                           0
city                                 0
country                              0
neutral_location                     0
shoot_out                            0
home_team_result                     0
home_team_goalkeeper_score       15542
away_team_goalkeeper_score       15826
home_team_mean_defense_score     16134
home_team_mean_offense_score     15411
home_team_mean_midfield_score    15759
away_team_mean_defense_score     16357
away_team_mean_offense_score     15609
away_team_mean_midfield_score    15942
dtype: int64

### At first glance i notice problems with the features:
1. date - i will have to convert this to just year maybe
2. home_team, away_team, home_team_continent, away_team_continent - i could do one hot encoding for these
3. tournament, city, country - again, one hot encoding
4. neutral_location - binary therefore i can make it 1/0
5. shoot_out - do not need this feature as it wont be available
6. the rest of the features have many many N/A values, a max of 16357 which is 68% of the dataset. unsure what to do about this, i will tackle this later

___

## last_scores exploration

In [117]:
last_scores

team        date  rank  goalkeeper_score  defense_score  \
0        Argentina  2022-06-05     4              84.0           82.0   
1        Australia  2022-06-13    42              77.0           72.0   
2          Belgium  2022-06-14     2              89.0           81.0   
3           Brazil  2022-06-06     1              89.0           87.0   
4         Cameroon  2022-06-09    37              67.0           77.0   
5           Canada  2022-06-13    38              76.0           69.0   
6       Costa Rica  2022-06-14    31              88.0           72.0   
7          Croatia  2022-06-13    16              82.0           78.0   
8          Denmark  2022-06-13    11              85.0           80.0   
9          Ecuador  2022-06-11    46              71.0           74.0   
10         England  2022-06-14     5              83.0           85.0   
11          France  2022-06-13     3              87.0           84.0   
12         Germany  2022-06-14    12              88.0           84.0   
13           Ghana  2022-06-14    60              74.0           76.0   
14         IR Iran  2022-06-12    21              73.0           69.0   
15           Japan  2022-06-14    23              73.0           75.0   
16  Korea Republic  2022-06-14    29              75.0           73.0   
17          Mexico  2022-06-14     9              80.0           77.0   
18         Morocco  2022-06-13    24              82.0           81.0   
19     Netherlands  2022-06-14    10              81.0           85.0   
20          Poland  2022-06-14    26              87.0           75.0   
21        Portugal  2022-06-12     8              82.0           85.0   
22           Qatar  2022-03-29    52              50.0           78.0   
23    Saudi Arabia  2022-06-09    49              70.0           73.0   
24         Senegal  2022-06-07    20              83.0           79.0   
25          Serbia  2022-06-12    25              80.0           76.0   
26           Spain  2022-06-12     7              84.0           86.0   
27     Switzerland  2022-06-12    14              85.0           78.0   
28         Tunisia  2022-06-14    35              64.0           71.0   
29             USA  2022-06-14    15              77.0           76.0   
30         Uruguay  2022-06-11    13              80.0           81.0   
31           Wales  2022-06-14    18              74.0           75.0   

    offense_score  midfield_score  
0            89.0            84.0  
1            72.0            74.0  
2            86.0            86.0  
3            87.0            86.0  
4            78.0            75.0  
5            73.0            78.0  
6            70.0            69.0  
7            77.0            84.0  
8            78.0            80.0  
9            76.0            74.0  
10           88.0            84.0  
11           87.0            86.0  
12           83.0            86.0  
13           76.0            78.0  
14           75.0            69.0  
15           75.0            78.0  
16           80.0            74.0  
17           83.0            78.0  
18           82.0            76.0  
19           83.0            84.0  
20           85.0            76.0  
21           86.0            84.0  
22           80.0            79.0  
23           68.0            73.0  
24           81.0            79.0  
25           80.0            82.0  
26           85.0            86.0  
27           77.0            80.0  
28           72.0            74.0  
29           78.0            76.0  
30           84.0            80.0  
31           73.0            78.0

### problems with data:
1. out of date: this is data from 2022-06. therefore i could probably update this following the link in the github

 ___

## players_22 exploration

In [118]:
players_22

sofifa_id                                         player_url  \
0         158023  https://sofifa.com/player/158023/lionel-messi/...   
1         188545  https://sofifa.com/player/188545/robert-lewand...   
2          20801  https://sofifa.com/player/20801/c-ronaldo-dos-...   
3         190871  https://sofifa.com/player/190871/neymar-da-sil...   
4         192985  https://sofifa.com/player/192985/kevin-de-bruy...   
...          ...                                                ...   
19234     261962  https://sofifa.com/player/261962/defu-song/220002   
19235     262040  https://sofifa.com/player/262040/caoimhin-port...   
19236     262760  https://sofifa.com/player/262760/nathan-logue/...   
19237     262820  https://sofifa.com/player/262820/luke-rudden/2...   
19238     264540  https://sofifa.com/player/264540/emanuel-lalch...   

               short_name                            long_name  \
0                L. Messi       Lionel Andrés Messi Cuccittini   
1          R. Lewandowski                   Robert Lewandowski   
2       Cristiano Ronaldo  Cristiano Ronaldo dos Santos Aveiro   
3               Neymar Jr        Neymar da Silva Santos Júnior   
4            K. De Bruyne                      Kevin De Bruyne   
...                   ...                                  ...   
19234           Song Defu                                  宋德福   
19235           C. Porter                      Caoimhin Porter   
19236            N. Logue              Nathan Logue-Cunningham   
19237           L. Rudden                          Luke Rudden   
19238  E. Lalchhanchhuaha              Emanuel Lalchhanchhuaha   

      player_positions  overall  potential    value_eur  wage_eur  age  \
0           RW, ST, CF       93         93   78000000.0  320000.0   34   
1                   ST       92         92  119500000.0  270000.0   32   
2               ST, LW       91         91   45000000.0  270000.0   36   
3              LW, CAM       91         91  129000000.0  270000.0   29   
4              CM, CAM       91         91  125500000.0  350000.0   30   
...                ...      ...        ...          ...       ...  ...   
19234              CDM       47         52      70000.0    1000.0   22   
19235               CM       47         59     110000.0     500.0   19   
19236               CM       47         55     100000.0     500.0   21   
19237               ST       47         60     110000.0     500.0   19   
19238              CAM       47         60     110000.0     500.0   19   

              dob  height_cm  weight_kg  club_team_id            club_name  \
0      1987-06-24        170         72          73.0  Paris Saint-Germain   
1      1988-08-21        185         81          21.0    FC Bayern München   
2      1985-02-05        187         83          11.0    Manchester United   
3      1992-02-05        175         68          73.0  Paris Saint-Germain   
4      1991-06-28        181         70          10.0      Manchester City   
...           ...        ...        ...           ...                  ...   
19234  1999-01-02        180         64      112541.0             Wuhan FC   
19235  2002-03-18        175         70         445.0           Derry City   
19236  2000-02-07        178         72      111131.0           Finn Harps   
19237  2002-04-23        173         66      111131.0           Finn Harps   
19238  2002-02-06        167         61      113040.0  NorthEast United FC   

                          league_name  league_level club_position  \
0                      French Ligue 1           1.0            RW   
1                German 1. Bundesliga           1.0            ST   
2              English Premier League           1.0            ST   
3                      French Ligue 1           1.0            LW   
4              English Premier League           1.0           RCM   
...                               ...           ...           ...   
19234            Chinese Super League           1.0 

### problems with data:
1. player id like player_url, short_name and long_name can be removed.(this is because sofifa_id is enough)
2. player_positions: I could either create a set of every player position and then one-hot encode it, or remove the feature. :UPDATE: can be removed as nation_position identifies their position, which is most useful.
3. dob can be removed (age already there)
4. club_name & league_name not useful i think
5. club_position - unsure how useful, can probably be removed
6. club_loaned_from,club_joined - useless
7. naitonality_name - useless (already identified by id)
8. nation_position - one hot encoding
9. preferred_foot - binary therefore can be converted to 1s, 0s
10. work_rate - one hot encoding
11. body_type - one hot encoding
12. real_face, player_tags, player_traits - can be removed
13. goalkeeping_speed - NANS converted to 0
14. player_face_url, club_logo_url, club_flag_url, nation_logo_url, nation_flag_url - removed
15. features such as lm,lcm,cm,rcm,rm et.c have data such as 66+3: not sure how to work with this. will have to figure this out

 ___

## gr_st (group stage) exploration 

In [119]:
gr_st

country1     country2 group
0     Qatar      Ecuador     a
1   Senegal  Netherlands     a
2   England      IR Iran     b
3       USA        Wales     b
4    France    Australia     d
..      ...          ...   ...
59       v1           v2    x2
60       w1           w2    y1
61       x1           x2    y2
62       y1           y2     f
63       z1           z2    f3

[64 rows x 3 columns]

### notes:
This dataset will be more useful for the simulation of the world cup rather than the actual model, therefore no data cleaning is needed

 ___

## sq_stats (squad stats) exploration

In [120]:
sq_stats

nationality_name   overall  potential
0            France  85.55000  89.180000
1           England  85.18000  89.000000
2             Spain  85.55000  88.360000
3            Brazil  85.64000  88.090000
4          Portugal  85.00000  88.000000
5           Germany  85.00000  87.550000
6       Netherlands  83.36000  87.000000
7         Argentina  83.73000  86.180000
8           Belgium  83.45000  85.550000
9           Uruguay  80.55000  84.640000
10          Croatia  80.27000  84.360000
11              USA  76.27000  83.730000
12          Denmark  79.91000  83.180000
13           Mexico  78.45000  82.910000
14          Senegal  79.73000  82.820000
15           Poland  79.18000  82.820000
16            Qatar  78.93036  82.629137
17      Switzerland  79.09000  82.550000
18           Serbia  77.45000  81.640000
19          Morocco  79.55000  81.450000
20            Japan  75.55000  80.450000
21            Ghana  76.27000  80.090000
22            Wales  75.36000  80.000000
23          Ecuador  73.09000  79.910000
24   Korea Republic  75.27000  79.000000
25         Cameroon  75.09000  78.910000
26           Canada  73.64000  78.450000
27        Australia  72.55000  76.820000
28          Tunisia  73.00000  76.000000
29     Saudi Arabia  71.45000  75.270000
30       Costa Rica  72.00000  74.550000
31          IR Iran  70.82000  72.360000

### notes:
data may be outdated: i will look into the source of these stats and update them to more recent ones

 ___

## training exploration

In [121]:
training

Team1        Team2  Team1_FIFA_RANK  Team2_FIFA_RANK  \
0            Bolivia      Uruguay               59               22   
1             Brazil       Mexico                8               14   
2            Ecuador    Venezuela               35               94   
3           Paraguay    Argentina               67                5   
4             Sweden  Switzerland                4                3   
...              ...          ...              ...              ...   
9316     Netherlands        Wales               10               18   
9317          Poland      Belgium               26                2   
9318           Chile        Ghana               28               60   
9319           Japan      Tunisia               23               35   
9320  Korea Republic        Egypt               29               32   

      Team1_Result  Team1_Goalkeeper_Score  Team2_Goalkeeper_Score  \
0                1                    67.0                    79.0   
1                2                    86.0                    79.0   
2                1                    71.0                    68.0   
3                0                    74.0                    81.0   
4                0                    76.0                    81.0   
...            ...                     ...                     ...   
9316             1                    81.0                    74.0   
9317             0                    87.0                    89.0   
9318             0                    79.0                    74.0   
9319             0                    73.0                    64.0   
9320             1                    75.0                    70.0   

      Team1_Defense  Team1_Offense  Team1_Midfield  Team2_Defense  \
0              67.0           69.0            68.0           80.0   
1              86.0           86.0            85.0           77.0   
2              71.0           75.0            75.0           72.0   
3              75.0           78.0            74.0           83.0   
4              77.0           81.0            78.0           78.0   
...             ...            ...             ...            ...   
9316           85.0           83.0            84.0           75.0   
9317           75.0           85.0            76.0           81.0   
9318           76.0           77.0            78.0           76.0   
9319           75.0           75.0            78.0           71.0   
9320           73.0           80.0            74.0           70.0   

      Team2_Offense  Team2_Midfield  
0              83.0            79.0  
1              79.0            78.0  
2              75.0            73.0  
3              88.0            85.0  
4              76.0            79.0  
...             ...             ...  
9316           73.0            78.0  
9317           86.0            86.0  
9318           76.0            78.0  
9319           72.0            74.0  
9320           79.0            71.0  

[9321 rows x 13 columns]

### notes:
1. teams could be turned into one-hot encoding


----

 ___

# Data cleaning

## Int_mat (international matches) 

### Todo
1. date - convert date to year
2. home_team, away_team, home_team_continent, away_team_continent, tournament, city, country - one-hot encode these
4. neutral_location - turn to binary integers
5. shoot_out - remove feature
6. figure out what to do with 68% NA data points


### Sources used
1. https://stackoverflow.com/questions/25146121/extracting-just-month-and-year-separately-from-pandas-datetime-column
2. https://www.educative.io/answers/how-to-delete-a-column-in-pandas
3. https://stackoverflow.com/questions/17383094/how-can-i-map-true-false-to-1-0-in-a-pandas-dataframe
4. https://stackoverflow.com/questions/40901770/is-there-a-simple-way-to-change-a-column-of-yes-no-to-1-0-in-a-pandas-dataframe
5. https://stackoverflow.com/questions/37292872/how-can-i-one-hot-encode-in-python
6. https://www.folkstalk.com/2022/10/pandas-add-suffix-to-column-names-with-code-examples.html
7. https://pandas.pydata.org/docs/user_guide/merging.html
8. https://www.geeksforgeeks.org/replace-nan-values-with-zeros-in-pandas-dataframe/
9. World cup -2nd attempt bookmaker data.ipynb

In [122]:
int_mat


date       home_team     away_team home_team_continent  \
0      1993-08-08         Bolivia       Uruguay       South America   
1      1993-08-08          Brazil        Mexico       South America   
2      1993-08-08         Ecuador     Venezuela       South America   
3      1993-08-08          Guinea  Sierra Leone              Africa   
4      1993-08-08        Paraguay     Argentina       South America   
...           ...             ...           ...                 ...   
23916  2022-06-14         Moldova       Andorra              Europe   
23917  2022-06-14   Liechtenstein        Latvia              Europe   
23918  2022-06-14           Chile         Ghana       South America   
23919  2022-06-14           Japan       Tunisia                Asia   
23920  2022-06-14  Korea Republic         Egypt                Asia   

      away_team_continent  home_team_fifa_rank  away_team_fifa_rank  \
0           South America                   59                   22   
1           North America                    8                   14   
2           South America                   35                   94   
3                  Africa                   65                   86   
4           South America                   67                    5   
...                   ...                  ...                  ...   
23916              Europe                  180                  153   
23917              Europe                  192                  135   
23918              Africa                   28                   60   
23919              Africa                   23                   35   
23920              Africa                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  away_team_score                    tournament  \
0                    3                1  FIFA World Cup qualification   
1                    1                1                      Friendly   
2                    5                0  FIFA World Cup qualification   
3                    1                0                      Friendly   
4                    1                3  FIFA World Cup qualification   
...                ...              ...                           ...   
23916                2                1           UEFA Nations League   
23917                0                2           UEFA Nations League   
23918                0                0                     Kirin Cup   
23919                0                3                     Kirin Cup   
23920                4                1                      Friendly   

           city         country  neutral_location shoot_out home_team_result  \
0        La Paz         Bolivia             False        No              Win   
1        Maceió          Brazil             False        No             Draw   
2         Quito         Ecuador             False        No              Win   
3       Conakry          Guinea             False        No              Win   
4      Asunción        Paraguay             False        No             Lose   
...         ...             ...               ...       ...              ...   
23916  Chișinău         Moldova             False        No      

In [123]:
int_mat['year'] = pd.DatetimeIndex(int_mat['date']).year
int_mat.drop('date', inplace=True, axis=1)

In [124]:
int_mat

home_team     away_team home_team_continent away_team_continent  \
0             Bolivia       Uruguay       South America       South America   
1              Brazil        Mexico       South America       North America   
2             Ecuador     Venezuela       South America       South America   
3              Guinea  Sierra Leone              Africa              Africa   
4            Paraguay     Argentina       South America       South America   
...               ...           ...                 ...                 ...   
23916         Moldova       Andorra              Europe              Europe   
23917   Liechtenstein        Latvia              Europe              Europe   
23918           Chile         Ghana       South America              Africa   
23919           Japan       Tunisia                Asia              Africa   
23920  Korea Republic         Egypt                Asia              Africa   

       home_team_fifa_rank  away_team_fifa_rank  home_team_total_fifa_points  \
0                       59                   22                            0   
1                        8                   14                            0   
2                       35                   94                            0   
3                       65                   86                            0   
4                       67                    5                            0   
...                    ...                  ...                          ...   
23916                  180                  153                          932   
23917                  192                  135                          895   
23918                   28                   60                         1526   
23919                   23                   35                         1553   
23920                   29                   32                         1519   

       away_team_total_fifa_points  home_team_score  away_team_score  \
0                                0                3                1   
1                                0                1                1   
2                                0                5                0   
3                                0                1                0   
4                                0                1                3   
...                            ...              ...              ...   
23916                         1040                2                1   
23917                         1105                0                2   
23918                         1387                0                0   
23919                         1499                0                3   
23920                         1500                4                1   

                         tournament      city         country  \
0      FIFA World Cup qualification    La Paz         Bolivia   
1                          Friendly    Maceió          Brazil   
2      FIFA World Cup qualification     Quito         Ecuador   
3                          Friendly   Conakry          Guinea   
4      FIFA World Cup qualification  Asunción        Paraguay   
...                             ...       ...             ...   
23916           UEFA Nations League  Chișinău         Moldova   
23917           UEFA Nations League     Vaduz   Liechtenstein   
23918                     Kirin Cup     Suita           Japan   
23919                     Kirin Cup     Suita           Japan   
23920                      Friendly     Seoul  Korea Republic   

       neutral_location shoot_out home_team_result  \
0                 False        No              Win   
1                 False        No             Draw   
2                 False        No              Win   
3                 False        No              Win   
4                 False        No             Lose   
...                 ...       ...              ...   
23916             False        No              Win   
23917             False 

In [125]:
int_mat["neutral_location"] = int_mat["neutral_location"].astype(int)
int_mat.drop('shoot_out', inplace=True, axis=1)
int_mat["home_team_result"].replace(('Win', 'Draw',"Lose"), (1, 0, -1), inplace=True)

In [126]:
int_mat

home_team     away_team home_team_continent away_team_continent  \
0             Bolivia       Uruguay       South America       South America   
1              Brazil        Mexico       South America       North America   
2             Ecuador     Venezuela       South America       South America   
3              Guinea  Sierra Leone              Africa              Africa   
4            Paraguay     Argentina       South America       South America   
...               ...           ...                 ...                 ...   
23916         Moldova       Andorra              Europe              Europe   
23917   Liechtenstein        Latvia              Europe              Europe   
23918           Chile         Ghana       South America              Africa   
23919           Japan       Tunisia                Asia              Africa   
23920  Korea Republic         Egypt                Asia              Africa   

       home_team_fifa_rank  away_team_fifa_rank  home_team_total_fifa_points  \
0                       59                   22                            0   
1                        8                   14                            0   
2                       35                   94                            0   
3                       65                   86                            0   
4                       67                    5                            0   
...                    ...                  ...                          ...   
23916                  180                  153                          932   
23917                  192                  135                          895   
23918                   28                   60                         1526   
23919                   23                   35                         1553   
23920                   29                   32                         1519   

       away_team_total_fifa_points  home_team_score  away_team_score  \
0                                0                3                1   
1                                0                1                1   
2                                0                5                0   
3                                0                1                0   
4                                0                1                3   
...                            ...              ...              ...   
23916                         1040                2                1   
23917                         1105                0                2   
23918                         1387                0                0   
23919                         1499                0                3   
23920                         1500                4                1   

                         tournament      city         country  \
0      FIFA World Cup qualification    La Paz         Bolivia   
1                          Friendly    Maceió          Brazil   
2      FIFA World Cup qualification     Quito         Ecuador   
3                          Friendly   Conakry          Guinea   
4      FIFA World Cup qualification  Asunción        Paraguay   
...                             ...       ...             ...   
23916           UEFA Nations League  Chișinău         Moldova   
23917           UEFA Nations League     Vaduz   Liechtenstein   
23918                     Kirin Cup     Suita           Japan   
23919                     Kirin Cup     Suita           Japan   
23920                      Friendly     Seoul  Korea Republic   

       neutral_location  home_team_result  home_team_goalkeeper_score  \
0                     0                 1                         NaN   
1                     0                 0                         NaN   
2                     0                 1                         NaN   
3                     0                 1                         NaN   
4                     0                -1                         NaN   
...               

In [127]:
#time to one-hot encode!
one_hot_home_team = pd.get_dummies(int_mat['home_team'])
one_hot_away_team = pd.get_dummies(int_mat['away_team'])
one_hot_home_team_continent = pd.get_dummies(int_mat['home_team_continent'])
one_hot_away_team_continent = pd.get_dummies(int_mat['home_team_continent'])

In [128]:

one_hot_home_team.columns = [str(col) + '_home_team' for col in one_hot_home_team.columns]
one_hot_home_team_continent.columns = [str(col) + '_home_team_continent' for col in one_hot_home_team_continent.columns]

one_hot_away_team.columns = [str(col) + '_away_team' for col in one_hot_away_team.columns]
one_hot_away_team_continent.columns = [str(col) + '_home_team_continent' for col in one_hot_away_team_continent.columns]

In [129]:
one_hot_home_team

Afghanistan_home_team  Albania_home_team  Algeria_home_team  \
0                          0                  0                  0   
1                          0                  0                  0   
2                          0                  0                  0   
3                          0                  0                  0   
4                          0                  0                  0   
...                      ...                ...                ...   
23916                      0                  0                  0   
23917                      0                  0                  0   
23918                      0                  0                  0   
23919                      0                  0                  0   
23920                      0                  0                  0   

       American Samoa_home_team  Andorra_home_team  Angola_home_team  \
0                             0                  0                 0   
1                             0                  0                 0   
2                             0                  0                 0   
3                             0                  0                 0   
4                             0                  0                 0   
...                         ...                ...               ...   
23916                         0                  0                 0   
23917                         0                  0                 0   
23918                         0                  0                 0   
23919                         0                  0                 0   
23920                         0                  0                 0   

       Anguilla_home_team  Antigua and Barbuda_home_team  Argentina_home_team  \
0                       0                              0                    0   
1                       0                              0                    0   
2                       0                              0                    0   
3                       0                              0                    0   
4                       0                              0                    0   
...                   ...                            ...                  ...   
23916                   0                              0                    0   
23917                   0                              0                    0   
23918                   0                              0                    0   
23919                   0                              0                    0   
23920                   0                              0                    0   

       Armenia_home_team  Aruba_home_team  Australia_home_team  \
0                      0                0                    0   
1                      0                0                    0   
2                      0                0                    0   
3                      0                0                    0   
4                      0                0                    0   
...                  ...              ...                  ...   
23916                  0                0                    0   
23917                  0                0                    0   
23918                  0                0                    0   
23919                  0                0                    0   
23920                  0                0                    0   

       Austria_home_team  Azerbaijan_home_team  Bahamas_home_team  \
0                      0                     0                  0   
1                      0                     0                  0   
2                      0                     0                  0   
3                      0                     0                  0   
4                      0                     0                  0   
...                  ...                   ...                ...   
23916                  0                     0      

In [130]:
one_hot_home_team_continent

Africa_home_team_continent  Asia_home_team_continent  \
0                               0                         0   
1                               0                         0   
2                               0                         0   
3                               1                         0   
4                               0                         0   
...                           ...                       ...   
23916                           0                         0   
23917                           0                         0   
23918                           0                         0   
23919                           0                         1   
23920                           0                         1   

       Europe_home_team_continent  North America_home_team_continent  \
0                               0                                  0   
1                               0                                  0   
2                               0                                  0   
3                               0                                  0   
4                               0                                  0   
...                           ...                                ...   
23916                           1                                  0   
23917                           1                                  0   
23918                           0                                  0   
23919                           0                                  0   
23920                           0                                  0   

       Oceania_home_team_continent  South America_home_team_continent  
0                                0                                  1  
1                                0                                  1  
2                                0                                  1  
3                                0                                  0  
4                                0                                  1  
...                            ...                                ...  
23916                            0                                  0  
23917                            0                                  0  
23918                            0                                  1  
23919                            0                                  0  
23920                            0                                  0  

[23921 rows x 6 columns]

In [131]:
one_hot_away_team

Afghanistan_away_team  Albania_away_team  Algeria_away_team  \
0                          0                  0                  0   
1                          0                  0                  0   
2                          0                  0                  0   
3                          0                  0                  0   
4                          0                  0                  0   
...                      ...                ...                ...   
23916                      0                  0                  0   
23917                      0                  0                  0   
23918                      0                  0                  0   
23919                      0                  0                  0   
23920                      0                  0                  0   

       American Samoa_away_team  Andorra_away_team  Angola_away_team  \
0                             0                  0                 0   
1                             0                  0                 0   
2                             0                  0                 0   
3                             0                  0                 0   
4                             0                  0                 0   
...                         ...                ...               ...   
23916                         0                  1                 0   
23917                         0                  0                 0   
23918                         0                  0                 0   
23919                         0                  0                 0   
23920                         0                  0                 0   

       Anguilla_away_team  Antigua and Barbuda_away_team  Argentina_away_team  \
0                       0                              0                    0   
1                       0                              0                    0   
2                       0                              0                    0   
3                       0                              0                    0   
4                       0                              0                    1   
...                   ...                            ...                  ...   
23916                   0                              0                    0   
23917                   0                              0                    0   
23918                   0                              0                    0   
23919                   0                              0                    0   
23920                   0                              0                    0   

       Armenia_away_team  Aruba_away_team  Australia_away_team  \
0                      0                0                    0   
1                      0                0                    0   
2                      0                0                    0   
3                      0                0                    0   
4                      0                0                    0   
...                  ...              ...                  ...   
23916                  0                0                    0   
23917                  0                0                    0   
23918                  0                0                    0   
23919                  0                0                    0   
23920                  0                0                    0   

       Austria_away_team  Azerbaijan_away_team  Bahamas_away_team  \
0                      0                     0                  0   
1                      0                     0                  0   
2                      0                     0                  0   
3                      0                     0                  0   
4                      0                     0                  0   
...                  ...                   ...                ...   
23916                  0                     0      

In [132]:
one_hot_away_team_continent

Africa_home_team_continent  Asia_home_team_continent  \
0                               0                         0   
1                               0                         0   
2                               0                         0   
3                               1                         0   
4                               0                         0   
...                           ...                       ...   
23916                           0                         0   
23917                           0                         0   
23918                           0                         0   
23919                           0                         1   
23920                           0                         1   

       Europe_home_team_continent  North America_home_team_continent  \
0                               0                                  0   
1                               0                                  0   
2                               0                                  0   
3                               0                                  0   
4                               0                                  0   
...                           ...                                ...   
23916                           1                                  0   
23917                           1                                  0   
23918                           0                                  0   
23919                           0                                  0   
23920                           0                                  0   

       Oceania_home_team_continent  South America_home_team_continent  
0                                0                                  1  
1                                0                                  1  
2                                0                                  1  
3                                0                                  0  
4                                0                                  1  
...                            ...                                ...  
23916                            0                                  0  
23917                            0                                  0  
23918                            0                                  1  
23919                            0                                  0  
23920                            0                                  0  

[23921 rows x 6 columns]

adding these would add a total of 434 columns

In [133]:
int_mat = pd.concat([int_mat, one_hot_home_team, one_hot_home_team_continent, one_hot_away_team, one_hot_away_team_continent], axis=1, join="inner")

In [134]:
int_mat

home_team     away_team home_team_continent away_team_continent  \
0             Bolivia       Uruguay       South America       South America   
1              Brazil        Mexico       South America       North America   
2             Ecuador     Venezuela       South America       South America   
3              Guinea  Sierra Leone              Africa              Africa   
4            Paraguay     Argentina       South America       South America   
...               ...           ...                 ...                 ...   
23916         Moldova       Andorra              Europe              Europe   
23917   Liechtenstein        Latvia              Europe              Europe   
23918           Chile         Ghana       South America              Africa   
23919           Japan       Tunisia                Asia              Africa   
23920  Korea Republic         Egypt                Asia              Africa   

       home_team_fifa_rank  away_team_fifa_rank  home_team_total_fifa_points  \
0                       59                   22                            0   
1                        8                   14                            0   
2                       35                   94                            0   
3                       65                   86                            0   
4                       67                    5                            0   
...                    ...                  ...                          ...   
23916                  180                  153                          932   
23917                  192                  135                          895   
23918                   28                   60                         1526   
23919                   23                   35                         1553   
23920                   29                   32                         1519   

       away_team_total_fifa_points  home_team_score  away_team_score  \
0                                0                3                1   
1                                0                1                1   
2                                0                5                0   
3                                0                1                0   
4                                0                1                3   
...                            ...              ...              ...   
23916                         1040                2                1   
23917                         1105                0                2   
23918                         1387                0                0   
23919                         1499                0                3   
23920                         1500                4                1   

                         tournament      city         country  \
0      FIFA World Cup qualification    La Paz         Bolivia   
1                          Friendly    Maceió          Brazil   
2      FIFA World Cup qualification     Quito         Ecuador   
3                          Friendly   Conakry          Guinea   
4      FIFA World Cup qualification  Asunción        Paraguay   
...                             ...       ...             ...   
23916           UEFA Nations League  Chișinău         Moldova   
23917           UEFA Nations League     Vaduz   Liechtenstein   
23918                     Kirin Cup     Suita           Japan   
23919                     Kirin Cup     Suita           Japan   
23920                      Friendly     Seoul  Korea Republic   

       neutral_location  home_team_result  home_team_goalkeeper_score  \
0                     0                 1                         NaN   
1                     0                 0                         NaN   
2                     0                 1                         NaN   
3                     0                 1                         NaN   
4                     0                -1                         NaN   
...               

In [135]:
NAColumns = []
for i in int_mat:
    sum = str(int_mat[i].isna().sum())
    print("N/A: "+ i + " has " + sum)
    if int(sum) != 0:
        NAColumns.append(i)

N/A: home_team has 0
N/A: away_team has 0
N/A: home_team_continent has 0
N/A: away_team_continent has 0
N/A: home_team_fifa_rank has 0
N/A: away_team_fifa_rank has 0
N/A: home_team_total_fifa_points has 0
N/A: away_team_total_fifa_points has 0
N/A: home_team_score has 0
N/A: away_team_score has 0
N/A: tournament has 0
N/A: city has 0
N/A: country has 0
N/A: neutral_location has 0
N/A: home_team_result has 0
N/A: home_team_goalkeeper_score has 15542
N/A: away_team_goalkeeper_score has 15826
N/A: home_team_mean_defense_score has 16134
N/A: home_team_mean_offense_score has 15411
N/A: home_team_mean_midfield_score has 15759
N/A: away_team_mean_defense_score has 16357
N/A: away_team_mean_offense_score has 15609
N/A: away_team_mean_midfield_score has 15942
N/A: year has 0
N/A: Afghanistan_home_team has 0
N/A: Albania_home_team has 0
N/A: Algeria_home_team has 0
N/A: American Samoa_home_team has 0
N/A: Andorra_home_team has 0
N/A: Angola_home_team has 0
N/A: Anguilla_home_team has 0
N/A: Anti

ValueError: invalid literal for int() with base 10: 'Africa_home_team_continent    0\nAfrica_home_team_continent    0\ndtype: int64'

In [136]:
for i in NAColumns:
    column_average = int_mat[i].mean()
    int_mat[i] = int_mat[i].fillna(column_average)

In [137]:

int_mat.drop('home_team_continent', inplace=True, axis=1)
int_mat.drop('away_team_continent', inplace=True, axis=1)

In [138]:
int_mat

home_team     away_team  home_team_fifa_rank  away_team_fifa_rank  \
0             Bolivia       Uruguay                   59                   22   
1              Brazil        Mexico                    8                   14   
2             Ecuador     Venezuela                   35                   94   
3              Guinea  Sierra Leone                   65                   86   
4            Paraguay     Argentina                   67                    5   
...               ...           ...                  ...                  ...   
23916         Moldova       Andorra                  180                  153   
23917   Liechtenstein        Latvia                  192                  135   
23918           Chile         Ghana                   28                   60   
23919           Japan       Tunisia                   23                   35   
23920  Korea Republic         Egypt                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  away_team_score                    tournament  \
0                    3                1  FIFA World Cup qualification   
1                    1                1                      Friendly   
2                    5                0  FIFA World Cup qualification   
3                    1                0                      Friendly   
4                    1                3  FIFA World Cup qualification   
...                ...              ...                           ...   
23916                2                1           UEFA Nations League   
23917                0                2           UEFA Nations League   
23918                0                0                     Kirin Cup   
23919                0                3                     Kirin Cup   
23920                4                1                      Friendly   

           city         country  neutral_location  home_team_result  \
0        La Paz         Bolivia                 0                 1   
1        Maceió          Brazil                 0                 0   
2         Quito         Ecuador                 0                 1   
3       Conakry          Guinea                 0                 1   
4      Asunción        Paraguay                 0                -1   
...         ...             ...               ...               ...   
23916  Chișinău         Moldova                 0                 1   
23917     Vaduz   Liechtenstein                 0                -1   
23918     Suita           Japan                 1                -1   
23919     Suita           Japan                 0                -1   
23920     Seoul  Korea Republic                 0                 1   

       home_team_goalkeeper_score  away_team_goalkeeper_score  \
0                       74.963838                   74.212477   
1                       74.963838                   74.212477   
2                       74.963838                   74.212477   
3                       74.963838                   74.212477   
4                       74.963838                   74.212477   
...                           ...                         ...   
23916                   65.000000                

## int_mat data cleaning done!
all thats left is to remove home_team and away_team, however i'm keeping them there to still have a legible data set i can undrestand

___

## players_22 data cleaning

### Todo
1. remove: player_url, short_name, long_name, player_positions, dob, club_name, league_name, club_position, club_loaned_from,  club_joined, nationality_name, real_face, player_tags, player_traits, player_face_url, club_logo_url, club_flag_url, nation_logo_url, nation_flag_url
2. one hot encode: nation_position, work_rate, body_type 
3. convert: preferred_foot to 1s, 0s
4. goalkeeping_speed - convert NANs to 0
5. features such as lm,lcm,cm,rcm,rm et.c have data such as 66+3: not sure how to work with this. figure this out

### Sources used
1. https://www.programiz.com/python-programming/exception-handling
2. https://towardsdatascience.com/7-ways-to-handle-missing-values-in-machine-learning-1a6326adf79e

In [139]:
players_22

sofifa_id                                         player_url  \
0         158023  https://sofifa.com/player/158023/lionel-messi/...   
1         188545  https://sofifa.com/player/188545/robert-lewand...   
2          20801  https://sofifa.com/player/20801/c-ronaldo-dos-...   
3         190871  https://sofifa.com/player/190871/neymar-da-sil...   
4         192985  https://sofifa.com/player/192985/kevin-de-bruy...   
...          ...                                                ...   
19234     261962  https://sofifa.com/player/261962/defu-song/220002   
19235     262040  https://sofifa.com/player/262040/caoimhin-port...   
19236     262760  https://sofifa.com/player/262760/nathan-logue/...   
19237     262820  https://sofifa.com/player/262820/luke-rudden/2...   
19238     264540  https://sofifa.com/player/264540/emanuel-lalch...   

               short_name                            long_name  \
0                L. Messi       Lionel Andrés Messi Cuccittini   
1          R. Lewandowski                   Robert Lewandowski   
2       Cristiano Ronaldo  Cristiano Ronaldo dos Santos Aveiro   
3               Neymar Jr        Neymar da Silva Santos Júnior   
4            K. De Bruyne                      Kevin De Bruyne   
...                   ...                                  ...   
19234           Song Defu                                  宋德福   
19235           C. Porter                      Caoimhin Porter   
19236            N. Logue              Nathan Logue-Cunningham   
19237           L. Rudden                          Luke Rudden   
19238  E. Lalchhanchhuaha              Emanuel Lalchhanchhuaha   

      player_positions  overall  potential    value_eur  wage_eur  age  \
0           RW, ST, CF       93         93   78000000.0  320000.0   34   
1                   ST       92         92  119500000.0  270000.0   32   
2               ST, LW       91         91   45000000.0  270000.0   36   
3              LW, CAM       91         91  129000000.0  270000.0   29   
4              CM, CAM       91         91  125500000.0  350000.0   30   
...                ...      ...        ...          ...       ...  ...   
19234              CDM       47         52      70000.0    1000.0   22   
19235               CM       47         59     110000.0     500.0   19   
19236               CM       47         55     100000.0     500.0   21   
19237               ST       47         60     110000.0     500.0   19   
19238              CAM       47         60     110000.0     500.0   19   

              dob  height_cm  weight_kg  club_team_id            club_name  \
0      1987-06-24        170         72          73.0  Paris Saint-Germain   
1      1988-08-21        185         81          21.0    FC Bayern München   
2      1985-02-05        187         83          11.0    Manchester United   
3      1992-02-05        175         68          73.0  Paris Saint-Germain   
4      1991-06-28        181         70          10.0      Manchester City   
...           ...        ...        ...           ...                  ...   
19234  1999-01-02        180         64      112541.0             Wuhan FC   
19235  2002-03-18        175         70         445.0           Derry City   
19236  2000-02-07        178         72      111131.0           Finn Harps   
19237  2002-04-23        173         66      111131.0           Finn Harps   
19238  2002-02-06        167         61      113040.0  NorthEast United FC   

                          league_name  league_level club_position  \
0                      French Ligue 1           1.0            RW   
1                German 1. Bundesliga           1.0            ST   
2              English Premier League           1.0            ST   
3                      French Ligue 1           1.0            LW   
4              English Premier League           1.0           RCM   
...                               ...           ...           ...   
19234            Chinese Super League           1.0 

In [140]:
players_22
players_22.drop(["player_url", "short_name", "long_name", "player_positions", "dob", "club_name", "league_name", "club_position", "club_loaned_from", "club_joined", "real_face", "player_tags", "player_traits", "player_face_url", "club_logo_url", "club_flag_url", "nation_logo_url", "nation_flag_url"], axis=1, inplace=True)

In [141]:
players_22["preferred_foot"].replace(('Left', 'Right'), (1, -1), inplace=True)

In [142]:
players_22["work_rate"].unique()

array(['Medium/Low', 'High/Medium', 'High/Low', 'High/High',
       'Medium/Medium', 'Medium/High', 'Low/High', 'Low/Medium',
       'Low/Low'], dtype=object)

In [143]:
players_22["work_rate"].replace(('High/High','High/Medium', 'Medium/High','Medium/Medium','High/Low','Low/High','Medium/Low', 'Low/Medium','Low/Low'  ), (9,8,7,6,5,4,3,2,1), inplace=True)

In [144]:
players_22["work_rate"].unique()

array([3, 8, 5, 9, 6, 7, 4, 2, 1], dtype=int64)

In [145]:
players_22["body_type"].unique()

array(['Unique', 'Normal (170-185)', 'Lean (170-185)', 'Normal (185+)',
       'Lean (185+)', 'Normal (170-)', 'Stocky (185+)', 'Lean (170-)',
       'Stocky (170-185)', 'Stocky (170-)'], dtype=object)

going to later one-hot encode body_type as there is no ranking between them (unlike work_rate which i assumed the higher the better)

I want to remove the NA values for nation_team_id as we dont care about those who arent in the world cup

In [146]:
players_22["nation_team_id"].isna().sum()

18480

nevermind.

In [147]:
players_22['goalkeeping_speed'] = players_22['goalkeeping_speed'].fillna(0)

gonna remove the ends + from the weird y+x stats

In [148]:
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_jersey_number  \
0             72          73.0           1.0                30.0   
1             81          21.0           1.0                 9.0   
2             83          11.0           1.0                 7.0   
3             68          73.0           1.0                10.0   
4             70          10.0           1.0                17.0   
...          ...           ...           ...                 ...   
19234         64      112541.0           1.0                36.0   
19235         70         445.0           1.0                27.0   
19236         72      111131.0           1.0                31.0   
19237         66      111131.0           1.0                12.0   
19238         61      113040.0           1.0                13.0   

       club_contract_valid_until  nationality_id     nationality_name  \
0                         2023.0              52            Argentina   
1                         2023.0              37               Poland   
2                         2023.0              38             Portugal   
3                         2025.0              54               Brazil   
4                         2025.0               7              Belgium   
...                          ...             ...                  ...   
19234                     2021.0             155             China PR   
19235                     2021.0              25  Republic of Ireland   
19236                     2021.0              25  Republic of Ireland   
19237                     2021.0              25  Republic of Ireland   
19238                     2025.0             159                India   

       nation_team_id nation_position  nation_jersey_number  preferred_foot  \
0              1369.0              RW                  10.0               1   
1              1353.0              RS                   9.0              -1   
2              1354.0              ST                   7.0              -1   
3                 NaN             NaN                   NaN              -1   
4              1325.0             RCM                   7.0              -1   
...               ...             ...                   ...             ...   
19234             NaN             NaN                   NaN              -1   
19235             NaN             NaN                   NaN              -1   
19236             NaN             NaN                   NaN              -1   
19237             NaN             NaN                   NaN              -1   
19238             NaN             NaN                   NaN              -1   

       weak_foot  skill_moves  international_reputation  work_rate  \
0              4            4                         5          3   
1              4            4                         5          8   
2              4            5                         5          5   
3              5            5                         5          8   
4              5            4                         4          

In [149]:
for i in players_22.columns:
    try:
        players_22[i] = players_22[i].str.replace(r'+', '')
    except:
        pass
        


C:\Users\Lorand\AppData\Local\Temp\ipykernel_8376\363195385.py:3: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  players_22[i] = players_22[i].str.replace(r'+', '')


In [150]:
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_jersey_number  \
0             72          73.0           1.0                30.0   
1             81          21.0           1.0                 9.0   
2             83          11.0           1.0                 7.0   
3             68          73.0           1.0                10.0   
4             70          10.0           1.0                17.0   
...          ...           ...           ...                 ...   
19234         64      112541.0           1.0                36.0   
19235         70         445.0           1.0                27.0   
19236         72      111131.0           1.0                31.0   
19237         66      111131.0           1.0                12.0   
19238         61      113040.0           1.0                13.0   

       club_contract_valid_until  nationality_id     nationality_name  \
0                         2023.0              52            Argentina   
1                         2023.0              37               Poland   
2                         2023.0              38             Portugal   
3                         2025.0              54               Brazil   
4                         2025.0               7              Belgium   
...                          ...             ...                  ...   
19234                     2021.0             155             China PR   
19235                     2021.0              25  Republic of Ireland   
19236                     2021.0              25  Republic of Ireland   
19237                     2021.0              25  Republic of Ireland   
19238                     2025.0             159                India   

       nation_team_id nation_position  nation_jersey_number  preferred_foot  \
0              1369.0              RW                  10.0               1   
1              1353.0              RS                   9.0              -1   
2              1354.0              ST                   7.0              -1   
3                 NaN             NaN                   NaN              -1   
4              1325.0             RCM                   7.0              -1   
...               ...             ...                   ...             ...   
19234             NaN             NaN                   NaN              -1   
19235             NaN             NaN                   NaN              -1   
19236             NaN             NaN                   NaN              -1   
19237             NaN             NaN                   NaN              -1   
19238             NaN             NaN                   NaN              -1   

       weak_foot  skill_moves  international_reputation  work_rate  \
0              4            4                         5          3   
1              4            4                         5          8   
2              4            5                         5          5   
3              5            5                         5          8   
4              5            4                         4          

In [151]:
one_hot_nation_position = pd.get_dummies(players_22['nation_position'])
one_hot_body_type = pd.get_dummies(players_22['body_type'])
one_hot_nation_position.columns = [str(col) + '_nation_position' for col in one_hot_nation_position.columns]
one_hot_body_type.columns = [str(col) + '_body_type' for col in one_hot_body_type.columns]
players_22 = pd.concat([players_22,one_hot_nation_position, one_hot_body_type], axis=1, join="inner")
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_jersey_number  \
0             72          73.0           1.0                30.0   
1             81          21.0           1.0                 9.0   
2             83          11.0           1.0                 7.0   
3             68          73.0           1.0                10.0   
4             70          10.0           1.0                17.0   
...          ...           ...           ...                 ...   
19234         64      112541.0           1.0                36.0   
19235         70         445.0           1.0                27.0   
19236         72      111131.0           1.0                31.0   
19237         66      111131.0           1.0                12.0   
19238         61      113040.0           1.0                13.0   

       club_contract_valid_until  nationality_id     nationality_name  \
0                         2023.0              52            Argentina   
1                         2023.0              37               Poland   
2                         2023.0              38             Portugal   
3                         2025.0              54               Brazil   
4                         2025.0               7              Belgium   
...                          ...             ...                  ...   
19234                     2021.0             155             China PR   
19235                     2021.0              25  Republic of Ireland   
19236                     2021.0              25  Republic of Ireland   
19237                     2021.0              25  Republic of Ireland   
19238                     2025.0             159                India   

       nation_team_id nation_position  nation_jersey_number  preferred_foot  \
0              1369.0              RW                  10.0               1   
1              1353.0              RS                   9.0              -1   
2              1354.0              ST                   7.0              -1   
3                 NaN             NaN                   NaN              -1   
4              1325.0             RCM                   7.0              -1   
...               ...             ...                   ...             ...   
19234             NaN             NaN                   NaN              -1   
19235             NaN             NaN                   NaN              -1   
19236             NaN             NaN                   NaN              -1   
19237             NaN             NaN                   NaN              -1   
19238             NaN             NaN                   NaN              -1   

       weak_foot  skill_moves  international_reputation  work_rate  \
0              4            4                         5          3   
1              4            4                         5          8   
2              4            5                         5          5   
3              5            5                         5          8   
4              5            4                         4          

In [152]:
players_22.drop(["nation_position", "body_type"], inplace=True, axis=1) 

In [153]:
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_jersey_number  \
0             72          73.0           1.0                30.0   
1             81          21.0           1.0                 9.0   
2             83          11.0           1.0                 7.0   
3             68          73.0           1.0                10.0   
4             70          10.0           1.0                17.0   
...          ...           ...           ...                 ...   
19234         64      112541.0           1.0                36.0   
19235         70         445.0           1.0                27.0   
19236         72      111131.0           1.0                31.0   
19237         66      111131.0           1.0                12.0   
19238         61      113040.0           1.0                13.0   

       club_contract_valid_until  nationality_id     nationality_name  \
0                         2023.0              52            Argentina   
1                         2023.0              37               Poland   
2                         2023.0              38             Portugal   
3                         2025.0              54               Brazil   
4                         2025.0               7              Belgium   
...                          ...             ...                  ...   
19234                     2021.0             155             China PR   
19235                     2021.0              25  Republic of Ireland   
19236                     2021.0              25  Republic of Ireland   
19237                     2021.0              25  Republic of Ireland   
19238                     2025.0             159                India   

       nation_team_id  nation_jersey_number  preferred_foot  weak_foot  \
0              1369.0                  10.0               1          4   
1              1353.0                   9.0              -1          4   
2              1354.0                   7.0              -1          4   
3                 NaN                   NaN              -1          5   
4              1325.0                   7.0              -1          5   
...               ...                   ...             ...        ...   
19234             NaN                   NaN              -1          3   
19235             NaN                   NaN              -1          3   
19236             NaN                   NaN              -1          3   
19237             NaN                   NaN              -1          3   
19238             NaN                   NaN              -1          3   

       skill_moves  international_reputation  work_rate  release_clause_eur  \
0                4                         5          3         144300000.0   
1                4                         5          8         197200000.0   
2                5                         5          5          83300000.0   
3                5                         5          8         238700000.0   
4                4                         4          9         232200000.0   
.

im almost done with this dataset! I just need to figure out what to do with NAN values

In [154]:
NAColumns = []
for i in players_22:
    sum = str(players_22[i].isna().sum())
    print("N/A: "+ i + " has " + sum)
    if int(sum) != 0:
        NAColumns.append(i)

N/A: sofifa_id has 0
N/A: overall has 0
N/A: potential has 0
N/A: value_eur has 74
N/A: wage_eur has 61
N/A: age has 0
N/A: height_cm has 0
N/A: weight_kg has 0
N/A: club_team_id has 61
N/A: league_level has 61
N/A: club_jersey_number has 61
N/A: club_contract_valid_until has 61
N/A: nationality_id has 0
N/A: nationality_name has 0
N/A: nation_team_id has 18480
N/A: nation_jersey_number has 18480
N/A: preferred_foot has 0
N/A: weak_foot has 0
N/A: skill_moves has 0
N/A: international_reputation has 0
N/A: work_rate has 0
N/A: release_clause_eur has 1176
N/A: pace has 2132
N/A: shooting has 2132
N/A: passing has 2132
N/A: dribbling has 2132
N/A: defending has 2132
N/A: physic has 2132
N/A: attacking_crossing has 0
N/A: attacking_finishing has 0
N/A: attacking_heading_accuracy has 0
N/A: attacking_short_passing has 0
N/A: attacking_volleys has 0
N/A: skill_dribbling has 0
N/A: skill_curve has 0
N/A: skill_fk_accuracy has 0
N/A: skill_long_passing has 0
N/A: skill_ball_control has 0
N/A: 

1. N/A: release_clause_eur has 1176
2. N/A: pace has 2132
3. N/A: shooting has 2132
4. N/A: passing has 2132
5. N/A: dribbling has 2132
6. N/A: defending has 2132
7. N/A: physic has 2132
8. N/A: nation_team_id has 18480
9. N/A: nation_jersey_number has 18480
10. N/A: club_team_id has 61
11. N/A: league_level has 61
12. N/A: club_jersey_number has 61
13. N/A: club_contract_valid_until has 61
14. N/A: value_eur has 74
15. N/A: wage_eur has 61

In [155]:
players_22["release_clause_eur"]= players_22["release_clause_eur"].interpolate(method='linear', limit_direction='forward', axis=0)
players_22["value_eur"]= players_22["value_eur"].interpolate(method='linear', limit_direction='forward', axis=0)
players_22["wage_eur"]= players_22["wage_eur"].interpolate(method='linear', limit_direction='forward', axis=0)
players_22["league_level"]= players_22["league_level"].interpolate(method='linear', limit_direction='forward', axis=0)
players_22["physic"]= players_22["physic"].interpolate(method='linear', limit_direction='forward', axis=0)
players_22["defending"]= players_22["defending"].interpolate(method='linear', limit_direction='forward', axis=0)
players_22["dribbling"]= players_22["dribbling"].interpolate(method='linear', limit_direction='forward', axis=0)
players_22["passing"]= players_22["passing"].interpolate(method='linear', limit_direction='forward', axis=0)
players_22["shooting"]= players_22["shooting"].interpolate(method='linear', limit_direction='forward', axis=0)
players_22["pace"]= players_22["pace"].interpolate(method='linear', limit_direction='forward', axis=0)
players_22["shooting"]= players_22["shooting"].interpolate(method='linear', limit_direction='forward', axis=0)

In [156]:
NAColumns = []
for i in players_22:
    sum = str(players_22[i].isna().sum())
    print("N/A: "+ i + " has " + sum)
    if int(sum) != 0:
        NAColumns.append(i)

N/A: sofifa_id has 0
N/A: overall has 0
N/A: potential has 0
N/A: value_eur has 0
N/A: wage_eur has 0
N/A: age has 0
N/A: height_cm has 0
N/A: weight_kg has 0
N/A: club_team_id has 61
N/A: league_level has 0
N/A: club_jersey_number has 61
N/A: club_contract_valid_until has 61
N/A: nationality_id has 0
N/A: nationality_name has 0
N/A: nation_team_id has 18480
N/A: nation_jersey_number has 18480
N/A: preferred_foot has 0
N/A: weak_foot has 0
N/A: skill_moves has 0
N/A: international_reputation has 0
N/A: work_rate has 0
N/A: release_clause_eur has 0
N/A: pace has 0
N/A: shooting has 0
N/A: passing has 0
N/A: dribbling has 0
N/A: defending has 0
N/A: physic has 0
N/A: attacking_crossing has 0
N/A: attacking_finishing has 0
N/A: attacking_heading_accuracy has 0
N/A: attacking_short_passing has 0
N/A: attacking_volleys has 0
N/A: skill_dribbling has 0
N/A: skill_curve has 0
N/A: skill_fk_accuracy has 0
N/A: skill_long_passing has 0
N/A: skill_ball_control has 0
N/A: movement_acceleration ha

In [157]:
NAColumns

['club_team_id',
 'club_jersey_number',
 'club_contract_valid_until',
 'nation_team_id',
 'nation_jersey_number']

1. N/A: club_team_id has 61
2. N/A: club_jersey_number has 61
3. N/A: club_contract_valid_until has 61
4. N/A: nation_team_id has 18480
5. N/A: nation_jersey_number has 18480

In [158]:
players_22[players_22["club_team_id"].isna()]

sofifa_id  overall  potential   value_eur  wage_eur  age  height_cm  \
147       184087       83         83  24250000.0  103000.0   32        186   
416       197242       80         80  17250000.0   38000.0   31        187   
694       187607       78         78   9500000.0   49000.0   32        196   
926       200094       77         78   8250000.0   18000.0   28        184   
1146      154950       76         76   1850000.0   18000.0   37        180   
...          ...      ...        ...         ...       ...  ...        ...   
12269     183122       63         63    325000.0    2500.0   36        187   
12891     245685       63         68    762500.0    1500.0   21        187   
14199     259680       62         80    900000.0    4250.0   19        188   
14466     213094       61         61    337500.0    1500.0   28        181   
14654     241475       61         62    787500.0    2500.0   26        183   

       weight_kg  club_team_id  league_level  club_jersey_number  \
147           81           NaN           1.0                 NaN   
416           84           NaN           1.0                 NaN   
694           91           NaN           1.0                 NaN   
926           78           NaN           1.0                 NaN   
1146          75           NaN           1.0                 NaN   
...          ...           ...           ...                 ...   
12269         74           NaN           2.5                 NaN   
12891         82           NaN           2.0                 NaN   
14199         78           NaN           1.5                 NaN   
14466         71           NaN           1.5                 NaN   
14654         63           NaN           2.5                 NaN   

       club_contract_valid_until  nationality_id nationality_name  \
147                          NaN               7          Belgium   
416                          NaN              37           Poland   
694                          NaN              40           Russia   
926                          NaN              40           Russia   
1146                         NaN              40           Russia   
...                          ...             ...              ...   
12269                        NaN              24          Iceland   
12891                        NaN              17          Finland   
14199                        NaN             198      New Zealand   
14466                        NaN             198      New Zealand   
14654                        NaN              17          Finland   

       nation_team_id  nation_jersey_number  preferred_foot  weak_foot  \
147            1325.0                   2.0              -1          3   
416            1353.0                  10.0              -1          3   
694            1357.0                  22.0              -1          3   
926            1357.0                   7.0              -1          3   
1146           1357.0                  18.0               1          2   
...               ...                   ...             ...        ...   
12269          1341.0                   2.0              -1          3   
12891          1334.0                  24.0               1          2   
14199        111473.0                  17.0              -1          4   
14466        111473.0                  21.0              -1          2   
14654          1334.0                  13.0              -1          3   

       skill_moves  international_reputation  work_rate  release_clause_eur  \
147              2                         3          6        4.550000e+07   
416              3                         3          9        2.795000e+07   
694              3                         2          3        1.715000e+07   
926              3                         1          7        1.710000e+07   
1146             4                         2          8        3.300000e+06   
...            ...                       ...        ...      

In [159]:
players_22[players_22["club_team_id"].isna() & players_22["nation_team_id"].isna()]

Empty DataFrame
Columns: [sofifa_id, overall, potential, value_eur, wage_eur, age, height_cm, weight_kg, club_team_id, league_level, club_jersey_number, club_contract_valid_until, nationality_id, nationality_name, nation_team_id, nation_jersey_number, preferred_foot, weak_foot, skill_moves, international_reputation, work_rate, release_clause_eur, pace, shooting, passing, dribbling, defending, physic, attacking_crossing, attacking_finishing, attacking_heading_accuracy, attacking_short_passing, attacking_volleys, skill_dribbling, skill_curve, skill_fk_accuracy, skill_long_passing, skill_ball_control, movement_acceleration, movement_sprint_speed, movement_agility, movement_reactions, movement_balance, power_shot_power, power_jumping, power_stamina, power_strength, power_long_shots, mentality_aggression, mentality_interceptions, mentality_positioning, mentality_vision, mentality_penalties, mentality_composure, defending_marking_awareness, defending_standing_tackle, defending_sliding_tackle, goalkeeping_diving, goalkeeping_handling, goalkeeping_kicking, goalkeeping_positioning, goalkeeping_reflexes, goalkeeping_speed, ls, st, rs, lw, lf, cf, rf, rw, lam, cam, ram, lm, lcm, cm, rcm, rm, lwb, ldm, cdm, rdm, rwb, lb, lcb, cb, rcb, rb, gk, CAM_nation_position, CB_nation_position, CDM_nation_position, CF_nation_position, CM_nation_position, GK_nation_position, LAM_nation_position, LB_nation_position, LCB_nation_position, LCM_nation_position, ...]
Index: []

there are no players with both NAN club teams and NAN nation teams. This makes club_team_id NANS hard to deal with

In [160]:
players_22["club_contract_valid_until"]= players_22["club_contract_valid_until"].interpolate(method='linear', limit_direction='forward', axis=0)

In [161]:
players_22["club_jersey_number"] = players_22["club_jersey_number"].fillna(-3)
players_22["club_team_id"] = players_22["club_team_id"].fillna(-4)

filled it with -1 to make sure it does not match to any club_team_id: this way it can not be identified by any model or anything and wont match up with anything (dont think this thought process makes sense)
- in the end i just filled it with -3 & -4 to then later onehot encode it and remove the columns -3 & -4

In [162]:
NAColumns = []
for i in players_22:
    sum = str(players_22[i].isna().sum())
    print("N/A: "+ i + " has " + sum)
    if int(sum) != 0:
        NAColumns.append(i)

N/A: sofifa_id has 0
N/A: overall has 0
N/A: potential has 0
N/A: value_eur has 0
N/A: wage_eur has 0
N/A: age has 0
N/A: height_cm has 0
N/A: weight_kg has 0
N/A: club_team_id has 0
N/A: league_level has 0
N/A: club_jersey_number has 0
N/A: club_contract_valid_until has 0
N/A: nationality_id has 0
N/A: nationality_name has 0
N/A: nation_team_id has 18480
N/A: nation_jersey_number has 18480
N/A: preferred_foot has 0
N/A: weak_foot has 0
N/A: skill_moves has 0
N/A: international_reputation has 0
N/A: work_rate has 0
N/A: release_clause_eur has 0
N/A: pace has 0
N/A: shooting has 0
N/A: passing has 0
N/A: dribbling has 0
N/A: defending has 0
N/A: physic has 0
N/A: attacking_crossing has 0
N/A: attacking_finishing has 0
N/A: attacking_heading_accuracy has 0
N/A: attacking_short_passing has 0
N/A: attacking_volleys has 0
N/A: skill_dribbling has 0
N/A: skill_curve has 0
N/A: skill_fk_accuracy has 0
N/A: skill_long_passing has 0
N/A: skill_ball_control has 0
N/A: movement_acceleration has 0

In [163]:
NAColumns

['nation_team_id', 'nation_jersey_number']

In [164]:
#the commented code separates the data too 2 seperate tables one of which contain N/A values of nation_team_id and another which doesnt contain any N/A Values
#players_22_notWC = pd.DataFrame()
#cond = players_22.nation_team_id.isna()
#rows = players_22.loc[cond, :]
#players_22_notWC = players_22_notWC.append(rows, ignore_index=True)
#players_22.drop(rows.index, inplace=True)
#players_22

In [165]:
#players_22_notWC

In [166]:
#players_22_notWC.nation_team_id.isna().sum()

I was originally going to separate the n/a values of nation_team_id from the rest of the table and have 2 sepatate tables of data. However as nation_team_id is just identification of their team, i think it may be best just to assign a negative number to each N/A value: this i feel would have to do anyway at some point because i wouldnt be able to work with a dataset with different columns.

In the end actually i think one hot encoding is the best! This way i can just assign the NAN values to no column

In [167]:
players_22["nation_team_id"] = players_22["nation_team_id"].fillna(-1)
players_22["nation_jersey_number"] = players_22["nation_jersey_number"].fillna(-2)

In [168]:
one_hot_nation_team_id = pd.get_dummies(players_22['nation_team_id'])
one_hot_nation_jersey_number = pd.get_dummies(players_22['nation_jersey_number'])
one_hot_nation_team_id.columns = [str(col) + '_nation_team_id' for col in one_hot_nation_team_id.columns]
one_hot_nation_jersey_number.columns = [str(col) + '_nation_jersey_number' for col in one_hot_nation_jersey_number.columns]
players_22 = pd.concat([players_22,one_hot_nation_team_id, one_hot_nation_jersey_number], axis=1, join="inner")
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_jersey_number  \
0             72          73.0           1.0                30.0   
1             81          21.0           1.0                 9.0   
2             83          11.0           1.0                 7.0   
3             68          73.0           1.0                10.0   
4             70          10.0           1.0                17.0   
...          ...           ...           ...                 ...   
19234         64      112541.0           1.0                36.0   
19235         70         445.0           1.0                27.0   
19236         72      111131.0           1.0                31.0   
19237         66      111131.0           1.0                12.0   
19238         61      113040.0           1.0                13.0   

       club_contract_valid_until  nationality_id     nationality_name  \
0                         2023.0              52            Argentina   
1                         2023.0              37               Poland   
2                         2023.0              38             Portugal   
3                         2025.0              54               Brazil   
4                         2025.0               7              Belgium   
...                          ...             ...                  ...   
19234                     2021.0             155             China PR   
19235                     2021.0              25  Republic of Ireland   
19236                     2021.0              25  Republic of Ireland   
19237                     2021.0              25  Republic of Ireland   
19238                     2025.0             159                India   

       nation_team_id  nation_jersey_number  preferred_foot  weak_foot  \
0              1369.0                  10.0               1          4   
1              1353.0                   9.0              -1          4   
2              1354.0                   7.0              -1          4   
3                -1.0                  -2.0              -1          5   
4              1325.0                   7.0              -1          5   
...               ...                   ...             ...        ...   
19234            -1.0                  -2.0              -1          3   
19235            -1.0                  -2.0              -1          3   
19236            -1.0                  -2.0              -1          3   
19237            -1.0                  -2.0              -1          3   
19238            -1.0                  -2.0              -1          3   

       skill_moves  international_reputation  work_rate  release_clause_eur  \
0                4                         5          3         144300000.0   
1                4                         5          8         197200000.0   
2                5                         5          5          83300000.0   
3                5                         5          8         238700000.0   
4                4                         4          9         232200000.0   
.

In [169]:
players_22.drop(["-2.0_nation_jersey_number", "-1.0_nation_team_id"], inplace=True, axis=1) 

In [170]:
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_jersey_number  \
0             72          73.0           1.0                30.0   
1             81          21.0           1.0                 9.0   
2             83          11.0           1.0                 7.0   
3             68          73.0           1.0                10.0   
4             70          10.0           1.0                17.0   
...          ...           ...           ...                 ...   
19234         64      112541.0           1.0                36.0   
19235         70         445.0           1.0                27.0   
19236         72      111131.0           1.0                31.0   
19237         66      111131.0           1.0                12.0   
19238         61      113040.0           1.0                13.0   

       club_contract_valid_until  nationality_id     nationality_name  \
0                         2023.0              52            Argentina   
1                         2023.0              37               Poland   
2                         2023.0              38             Portugal   
3                         2025.0              54               Brazil   
4                         2025.0               7              Belgium   
...                          ...             ...                  ...   
19234                     2021.0             155             China PR   
19235                     2021.0              25  Republic of Ireland   
19236                     2021.0              25  Republic of Ireland   
19237                     2021.0              25  Republic of Ireland   
19238                     2025.0             159                India   

       nation_team_id  nation_jersey_number  preferred_foot  weak_foot  \
0              1369.0                  10.0               1          4   
1              1353.0                   9.0              -1          4   
2              1354.0                   7.0              -1          4   
3                -1.0                  -2.0              -1          5   
4              1325.0                   7.0              -1          5   
...               ...                   ...             ...        ...   
19234            -1.0                  -2.0              -1          3   
19235            -1.0                  -2.0              -1          3   
19236            -1.0                  -2.0              -1          3   
19237            -1.0                  -2.0              -1          3   
19238            -1.0                  -2.0              -1          3   

       skill_moves  international_reputation  work_rate  release_clause_eur  \
0                4                         5          3         144300000.0   
1                4                         5          8         197200000.0   
2                5                         5          5          83300000.0   
3                5                         5          8         238700000.0   
4                4                         4          9         232200000.0   
.

In [171]:
one_hot_club_jersey_number = pd.get_dummies(players_22['club_jersey_number'])
one_hot_club_team_id = pd.get_dummies(players_22['club_team_id'])
one_hot_club_jersey_number.columns = [str(col) + '_one_hot_club_jersey_number' for col in one_hot_club_jersey_number.columns]
one_hot_club_team_id.columns = [str(col) + '_one_hot_club_team_id' for col in one_hot_club_team_id.columns]
players_22 = pd.concat([players_22,one_hot_club_jersey_number, one_hot_club_team_id], axis=1, join="inner")
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_jersey_number  \
0             72          73.0           1.0                30.0   
1             81          21.0           1.0                 9.0   
2             83          11.0           1.0                 7.0   
3             68          73.0           1.0                10.0   
4             70          10.0           1.0                17.0   
...          ...           ...           ...                 ...   
19234         64      112541.0           1.0                36.0   
19235         70         445.0           1.0                27.0   
19236         72      111131.0           1.0                31.0   
19237         66      111131.0           1.0                12.0   
19238         61      113040.0           1.0                13.0   

       club_contract_valid_until  nationality_id     nationality_name  \
0                         2023.0              52            Argentina   
1                         2023.0              37               Poland   
2                         2023.0              38             Portugal   
3                         2025.0              54               Brazil   
4                         2025.0               7              Belgium   
...                          ...             ...                  ...   
19234                     2021.0             155             China PR   
19235                     2021.0              25  Republic of Ireland   
19236                     2021.0              25  Republic of Ireland   
19237                     2021.0              25  Republic of Ireland   
19238                     2025.0             159                India   

       nation_team_id  nation_jersey_number  preferred_foot  weak_foot  \
0              1369.0                  10.0               1          4   
1              1353.0                   9.0              -1          4   
2              1354.0                   7.0              -1          4   
3                -1.0                  -2.0              -1          5   
4              1325.0                   7.0              -1          5   
...               ...                   ...             ...        ...   
19234            -1.0                  -2.0              -1          3   
19235            -1.0                  -2.0              -1          3   
19236            -1.0                  -2.0              -1          3   
19237            -1.0                  -2.0              -1          3   
19238            -1.0                  -2.0              -1          3   

       skill_moves  international_reputation  work_rate  release_clause_eur  \
0                4                         5          3         144300000.0   
1                4                         5          8         197200000.0   
2                5                         5          5          83300000.0   
3                5                         5          8         238700000.0   
4                4                         4          9         232200000.0   
.

In [172]:
players_22.drop(["-4.0_one_hot_club_team_id", "-3.0_one_hot_club_jersey_number"], inplace=True, axis=1) 


In [173]:
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_jersey_number  \
0             72          73.0           1.0                30.0   
1             81          21.0           1.0                 9.0   
2             83          11.0           1.0                 7.0   
3             68          73.0           1.0                10.0   
4             70          10.0           1.0                17.0   
...          ...           ...           ...                 ...   
19234         64      112541.0           1.0                36.0   
19235         70         445.0           1.0                27.0   
19236         72      111131.0           1.0                31.0   
19237         66      111131.0           1.0                12.0   
19238         61      113040.0           1.0                13.0   

       club_contract_valid_until  nationality_id     nationality_name  \
0                         2023.0              52            Argentina   
1                         2023.0              37               Poland   
2                         2023.0              38             Portugal   
3                         2025.0              54               Brazil   
4                         2025.0               7              Belgium   
...                          ...             ...                  ...   
19234                     2021.0             155             China PR   
19235                     2021.0              25  Republic of Ireland   
19236                     2021.0              25  Republic of Ireland   
19237                     2021.0              25  Republic of Ireland   
19238                     2025.0             159                India   

       nation_team_id  nation_jersey_number  preferred_foot  weak_foot  \
0              1369.0                  10.0               1          4   
1              1353.0                   9.0              -1          4   
2              1354.0                   7.0              -1          4   
3                -1.0                  -2.0              -1          5   
4              1325.0                   7.0              -1          5   
...               ...                   ...             ...        ...   
19234            -1.0                  -2.0              -1          3   
19235            -1.0                  -2.0              -1          3   
19236            -1.0                  -2.0              -1          3   
19237            -1.0                  -2.0              -1          3   
19238            -1.0                  -2.0              -1          3   

       skill_moves  international_reputation  work_rate  release_clause_eur  \
0                4                         5          3         144300000.0   
1                4                         5          8         197200000.0   
2                5                         5          5          83300000.0   
3                5                         5          8         238700000.0   
4                4                         4          9         232200000.0   
.

i will need to drop club_team_id & nation_team_id at some point, however i will keep them now just for identification of the players so i can add them to other datasets and such, and i will drop them once i need to train the model

In [174]:
players_22.drop(["club_jersey_number", "nation_jersey_number"], inplace=True, axis=1)
#these are not needed for the logistics of datasets therefore im dropping them

## players_22 data cleaning done!
all thats left to do is remove club_team_id & nation_team_id

------------------

## last_scores data cleaning

### Todo 
1. update team rank (using https://www.fifa.com/fifa-world-ranking/men?dateId=id13792)
2. Create function from players_22 data to create the following stats for each team:
- average for every column of each player
- add to last_scores

### Sources used
1. https://stackoverflow.com/questions/38752444/get-mean-for-all-columns-in-a-dataframe-and-create-a-new-dataframe
2. https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.html
3. https://stackoverflow.com/questions/43175382/python-create-a-pandas-data-frame-from-a-list
4. https://stackoverflow.com/questions/21860605/python-remove-lists-from-list-of-lists-similar-functionality-to-pop
5. https://www.geeksforgeeks.org/python-convert-list-into-list-of-lists/
6. https://stackoverflow.com/questions/38604805/convert-list-into-list-of-lists
7. https://thispointer.com/pandas-drop-last-n-columns-of-dataframe/
8. https://stackoverflow.com/questions/46567449/set-a-string-as-index-of-pandas-dataframe
9. https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.append.html
10. https://stackoverflow.com/questions/44513738/pandas-create-empty-dataframe-with-only-column-names
11. https://www.educative.io/answers/how-to-delete-a-column-in-pandas
12. https://stackoverflow.com/questions/43190773/valueerror-length-mismatch-expected-axis-has-0-elements-while-creating-hierarc
13. https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.drop.html
14. https://stackoverflow.com/questions/69867084/add-new-columns-to-dataframe-based-on-index-from-another-dataframe-in-python
15. https://sparkbyexamples.com/pandas/pandas-set-index-name-to-dataframe/
16. https://towardsdatascience.com/7-ways-to-handle-missing-values-in-machine-learning-1a6326adf79e
17. https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.merge.html

In [175]:
last_scores


team        date  rank  goalkeeper_score  defense_score  \
0        Argentina  2022-06-05     4              84.0           82.0   
1        Australia  2022-06-13    42              77.0           72.0   
2          Belgium  2022-06-14     2              89.0           81.0   
3           Brazil  2022-06-06     1              89.0           87.0   
4         Cameroon  2022-06-09    37              67.0           77.0   
5           Canada  2022-06-13    38              76.0           69.0   
6       Costa Rica  2022-06-14    31              88.0           72.0   
7          Croatia  2022-06-13    16              82.0           78.0   
8          Denmark  2022-06-13    11              85.0           80.0   
9          Ecuador  2022-06-11    46              71.0           74.0   
10         England  2022-06-14     5              83.0           85.0   
11          France  2022-06-13     3              87.0           84.0   
12         Germany  2022-06-14    12              88.0           84.0   
13           Ghana  2022-06-14    60              74.0           76.0   
14         IR Iran  2022-06-12    21              73.0           69.0   
15           Japan  2022-06-14    23              73.0           75.0   
16  Korea Republic  2022-06-14    29              75.0           73.0   
17          Mexico  2022-06-14     9              80.0           77.0   
18         Morocco  2022-06-13    24              82.0           81.0   
19     Netherlands  2022-06-14    10              81.0           85.0   
20          Poland  2022-06-14    26              87.0           75.0   
21        Portugal  2022-06-12     8              82.0           85.0   
22           Qatar  2022-03-29    52              50.0           78.0   
23    Saudi Arabia  2022-06-09    49              70.0           73.0   
24         Senegal  2022-06-07    20              83.0           79.0   
25          Serbia  2022-06-12    25              80.0           76.0   
26           Spain  2022-06-12     7              84.0           86.0   
27     Switzerland  2022-06-12    14              85.0           78.0   
28         Tunisia  2022-06-14    35              64.0           71.0   
29             USA  2022-06-14    15              77.0           76.0   
30         Uruguay  2022-06-11    13              80.0           81.0   
31           Wales  2022-06-14    18              74.0           75.0   

    offense_score  midfield_score  
0            89.0            84.0  
1            72.0            74.0  
2            86.0            86.0  
3            87.0            86.0  
4            78.0            75.0  
5            73.0            78.0  
6            70.0            69.0  
7            77.0            84.0  
8            78.0            80.0  
9            76.0            74.0  
10           88.0            84.0  
11           87.0            86.0  
12           83.0            86.0  
13           76.0            78.0  
14           75.0            69.0  
15           75.0            78.0  
16           80.0            74.0  
17           83.0            78.0  
18           82.0            76.0  
19           83.0            84.0  
20           85.0            76.0  
21           86.0            84.0  
22           80.0            79.0  
23           68.0            73.0  
24           81.0            79.0  
25           80.0            82.0  
26           85.0            86.0  
27           77.0            80.0  
28           72.0            74.0  
29           78.0            76.0  
30           84.0            80.0  
31           73.0            78.0

In [176]:
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_contract_valid_until  \
0             72          73.0           1.0                     2023.0   
1             81          21.0           1.0                     2023.0   
2             83          11.0           1.0                     2023.0   
3             68          73.0           1.0                     2025.0   
4             70          10.0           1.0                     2025.0   
...          ...           ...           ...                        ...   
19234         64      112541.0           1.0                     2021.0   
19235         70         445.0           1.0                     2021.0   
19236         72      111131.0           1.0                     2021.0   
19237         66      111131.0           1.0                     2021.0   
19238         61      113040.0           1.0                     2025.0   

       nationality_id     nationality_name  nation_team_id  preferred_foot  \
0                  52            Argentina          1369.0               1   
1                  37               Poland          1353.0              -1   
2                  38             Portugal          1354.0              -1   
3                  54               Brazil            -1.0              -1   
4                   7              Belgium          1325.0              -1   
...               ...                  ...             ...             ...   
19234             155             China PR            -1.0              -1   
19235              25  Republic of Ireland            -1.0              -1   
19236              25  Republic of Ireland            -1.0              -1   
19237              25  Republic of Ireland            -1.0              -1   
19238             159                India            -1.0              -1   

       weak_foot  skill_moves  international_reputation  work_rate  \
0              4            4                         5          3   
1              4            4                         5          8   
2              4            5                         5          5   
3              5            5                         5          8   
4              5            4                         4          9   
...          ...          ...                       ...        ...   
19234          3            2                         1          6   
19235          3            2                         1          6   
19236          3            2                         1          6   
19237          3            2                         1          6   
19238          3            2                         1          6   

       release_clause_eur  pace  shooting  passing  dribbling  defending  \
0             144300000.0  85.0      92.0     91.0       95.0       34.0   
1             197200000.0  78.0      92.0     79.0       86.0       44.0   
2              83300000.0  87.0      94.0     80.0       88.0       34.0   
3             238700000.0  91.0      83.0     86.0       94.0       37.0   

In [177]:
players_22["nationality_name"].unique()

array(['Argentina', 'Poland', 'Portugal', 'Brazil', 'Belgium', 'Slovenia',
       'France', 'Germany', 'England', 'Korea Republic', 'Netherlands',
       'Senegal', 'Egypt', 'Italy', 'Spain', 'Uruguay', 'Costa Rica',
       'Norway', 'Croatia', 'Scotland', 'Algeria', 'Slovakia', 'Denmark',
       'Switzerland', 'Hungary', 'Gabon', 'Serbia', 'Nigeria', 'Morocco',
       'Sweden', 'Austria', 'Montenegro', "Côte d'Ivoire", 'Mexico',
       'Bosnia and Herzegovina', 'Finland', 'Greece', 'Armenia',
       'Colombia', 'Cameroon', 'Ghana', 'Wales', 'Russia', 'Turkey',
       'USA', 'Jamaica', 'Canada', 'Czech Republic', 'Chile', 'Ukraine',
       'Venezuela', 'Togo', 'Burkina Faso', 'Northern Ireland',
       'Congo DR', 'Israel', 'Albania', 'Guinea', 'Iceland', 'China PR',
       'New Zealand', 'Central African Republic', 'Peru', 'Mali', 'Japan',
       'North Macedonia', 'Ecuador', 'IR Iran', 'Republic of Ireland',
       'Angola', 'Romania', 'Mozambique', 'Cape Verde Islands',
       'Aust

In [178]:
teams = sq_stats["nationality_name"].tolist()
teams

['France',
 'England',
 'Spain',
 'Brazil',
 'Portugal',
 'Germany',
 'Netherlands',
 'Argentina',
 'Belgium',
 'Uruguay',
 'Croatia',
 'USA',
 'Denmark',
 'Mexico',
 'Senegal',
 'Poland',
 'Qatar',
 'Switzerland',
 'Serbia',
 'Morocco',
 'Japan',
 'Ghana',
 'Wales',
 'Ecuador',
 'Korea Republic',
 'Cameroon',
 'Canada',
 'Australia',
 'Tunisia',
 'Saudi Arabia',
 'Costa Rica',
 'IR Iran']

In [179]:
for i in teams:
    print(i)
    print(players_22[players_22["nationality_name"]==i]["nation_team_id"].unique())

France
[ 1.335e+03 -1.000e+00]
England
[ 1.318e+03 -1.000e+00]
Spain
[ 1.362e+03 -1.000e+00]
Brazil
[-1.00e+00  1.37e+03]
Portugal
[ 1.354e+03 -1.000e+00]
Germany
[ 1.337e+03 -1.000e+00]
Netherlands
[ 1.05035e+05 -1.00000e+00]
Argentina
[ 1.369e+03 -1.000e+00]
Belgium
[ 1.325e+03 -1.000e+00]
Uruguay
[-1.]
Croatia
[-1.]
USA
[ 1.387e+03 -1.000e+00]
Denmark
[ 1.331e+03 -1.000e+00]
Mexico
[-1.000e+00  1.386e+03]
Senegal
[-1.]
Poland
[ 1.353e+03 -1.000e+00]
Qatar
[]
Switzerland
[-1.]
Serbia
[-1.]
Morocco
[-1.]
Japan
[-1.]
Ghana
[-1.]
Wales
[ 1.367e+03 -1.000e+00]
Ecuador
[-1.]
Korea Republic
[-1.]
Cameroon
[-1.]
Canada
[ 1.11455e+05 -1.00000e+00]
Australia
[ 1.415e+03 -1.000e+00]
Tunisia
[-1.]
Saudi Arabia
[-1.]
Costa Rica
[-1.]
IR Iran
[-1.]


15/32 teams dont have nation team IDS, therefore this makes it hard to get stats for thema as their players are not identified.

the following teams have team_ids, therefore identified players:
- Canada, Australia, Wales, Poland, USA, Denmark, Mexico, France, England, Spain, Brazil, Portugal, Germany, Netherlands, Argentina, Belgium


the rest of the teams dont. Therefore, if a team is identified by an id, i will get the averagek stats of the teams players. otherwise, i will just get the average stats of every player with the nationality

In [180]:
teams_w_id = ["Canada", "Australia", "Wales", "Poland", "USA", "Denmark", "Mexico", "France", "England", "Spain", "Brazil", "Portugal", "Germany", "Netherlands", "Argentina", "Belgium"]
teams_wo_id = ["Uruguay", "Croatia", "Senegal", "Qatar", "Switzerland", "Serbia", "Morocco", "Japan", "Ghana", "Ecuador", "Korea Republic", "Cameroon", "Tunisia", "Saudi Arabia", "Costa Rica", "IR Iran"]


In [181]:
players_22[players_22["nationality_name"]=="Uruguay"]

sofifa_id  overall  potential   value_eur  wage_eur  age  height_cm  \
23        176580       88         88  44500000.0  135000.0   34        182   
74        179813       85         85  26000000.0  190000.0   34        185   
130       216460       84         88  52000000.0   74000.0   26        185   
159       197655       83         83  30000000.0   21000.0   30        196   
196       239053       83         89  58000000.0  160000.0   22        182   
...          ...      ...        ...         ...       ...  ...        ...   
18567     260737       53         64    190000.0     500.0   20        179   
18977     263431       51         63    130000.0     500.0   18        180   
19069     262050       50         65    100000.0     500.0   19        184   
19145     260699       49         68    120000.0     500.0   18        173   
19217     263394       48         55     90000.0     500.0   23        172   

       weight_kg  club_team_id  league_level  club_contract_valid_until  \
23            83         240.0           1.0                     2022.0   
74            77          11.0           1.0                     2022.0   
130           79         240.0           1.0                     2025.0   
159           92         237.0           1.0                     2023.0   
196           78         243.0           1.0                     2027.0   
...          ...           ...           ...                        ...   
18567         78      101110.0           1.0                     2021.0   
18977         70      111002.0           1.0                     2022.0   
19069         73      115535.0           1.0                     2021.0   
19145         65      115535.0           1.0                     2021.0   
19217         72      115536.0           1.0                     2022.0   

       nationality_id nationality_name  nation_team_id  preferred_foot  \
23                 60          Uruguay            -1.0              -1   
74                 60          Uruguay            -1.0              -1   
130                60          Uruguay            -1.0              -1   
159                60          Uruguay            -1.0              -1   
196                60          Uruguay            -1.0              -1   
...               ...              ...             ...             ...   
18567              60          Uruguay            -1.0              -1   
18977              60          Uruguay            -1.0              -1   
19069              60          Uruguay            -1.0              -1   
19145              60          Uruguay            -1.0              -1   
19217              60          Uruguay            -1.0              -1   

       weak_foot  skill_moves  international_reputation  work_rate  \
23             4            3                         5          8   
74             4            3                         4          9   
130            3            2                         2          7   
159            3            2                         3          6   
196            4            3                         1          9   
...          ...          ...                       ...        ...   
18567          2            2                         1          4   
18977          2            2                         1          2   
19069          2            2                         1          6   
19145          2            2                         1          6   
19217          3            2                         1          6   

       release_clause_eur  pace  shooting  passing  dribbling  defending  \
23             91200000.0  72.0      90.0     82.0       84.0       47.0   
74             48100000.0  66.0      86.0     70.0       76.0       51.0   
130           110500000.0  69.0      45.0     57.0       59.0       86.0   
159            60000000.0  68.0      49.0     55.0       63.0       84.0   
196           130500000.0  86.0      74.0     78.0       79

In [182]:
mean = players_22[players_22["nationality_name"]=="Uruguay"].mean()
print(mean)
new_df = pd.DataFrame(mean.to_dict(),index=[mean.index.values[-1]])
new_df

C:\Users\Lorand\AppData\Local\Temp\ipykernel_8376\2769600990.py:1: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  mean = players_22[players_22["nationality_name"]=="Uruguay"].mean()


sofifa_id                        2.384619e+05
overall                          6.727857e+01
potential                        7.158929e+01
value_eur                        3.293286e+06
wage_eur                         8.474286e+03
                                     ...     
115530.0_one_hot_club_team_id    0.000000e+00
115535.0_one_hot_club_team_id    8.928571e-02
115536.0_one_hot_club_team_id    6.428571e-02
115716.0_one_hot_club_team_id    0.000000e+00
115820.0_one_hot_club_team_id    0.000000e+00
Length: 968, dtype: float64


sofifa_id    overall  potential  \
115820.0_one_hot_club_team_id  238461.871429  67.278571  71.589286   

                                  value_eur     wage_eur        age  \
115820.0_one_hot_club_team_id  3.293286e+06  8474.285714  26.292857   

                                height_cm  weight_kg  club_team_id  \
115820.0_one_hot_club_team_id  179.846429     74.725     90924.825   

                               league_level  club_contract_valid_until  \
115820.0_one_hot_club_team_id      1.028571                2022.382143   

                               nationality_id  nation_team_id  preferred_foot  \
115820.0_one_hot_club_team_id            60.0            -1.0       -0.492857   

                               weak_foot  skill_moves  \
115820.0_one_hot_club_team_id   2.796429     2.339286   

                               international_reputation  work_rate  \
115820.0_one_hot_club_team_id                  1.092857   6.257143   

                               release_clause_eur       pace   shooting  \
115820.0_one_hot_club_team_id        6.593789e+06  66.621726  53.423512   

                                 passing  dribbling  defending  physic  \
115820.0_one_hot_club_team_id  57.541667  62.740179  52.055952   64.85   

                               attacking_crossing  attacking_finishing  \
115820.0_one_hot_club_team_id           49.185714            47.378571   

                               attacking_heading_accuracy  \
115820.0_one_hot_club_team_id                      54.275   

                               attacking_short_passing  attacking_volleys  \
115820.0_one_hot_club_team_id                60.178571          43.285714   

                               skill_dribbling  skill_curve  \
115820.0_one_hot_club_team_id             55.7    46.610714   

                               skill_fk_accuracy  skill_long_passing  \
115820.0_one_hot_club_team_id          44.071429                53.1   

                               skill_ball_control  movement_acceleration  \
115820.0_one_hot_club_team_id           60.535714              63.871429   

                               movement_sprint_speed  movement_agility  \
115820.0_one_hot_club_team_id              63.135714         62.132143   

                               movement_reactions  movement_balance  \
115820.0_one_hot_club_team_id           63.567857         63.407143   

                               power_shot_power  power_jumping  power_stamina  \
115820.0_one_hot_club_team_id         57.982143      64.753571         63.625   

                               power_strength  power_long_shots  \
115820.0_one_hot_club_team_id       65.007143         48.053571   

                               mentality_aggression  mentality_interceptions  \
115820.0_one_hot_club_team_id             56.871429                48.714286   

                               mentality_positioning  mentality_vision  \
115820.0_one_hot_club_team_id              51.939286         54.196429   

                               mentality_penalties  mentality_composure  \
115820.0_one_hot_club_team_id            49.639286            57.760714   

                               defending_marking_awareness  \
115820.0_one_hot_club_team_id                    47.035714   

                               defending_standing_tackle  \
115820.0_one_hot_club_team_id                  48.942857   

                               defending_sliding_tackle  goalkeeping_diving  \
115820.0_one_hot_club_team_id                 46.017857           15.496429   

                               goalkeeping_handling  goalkeeping_kicking  \
115820.0_one_hot_club_team_id             15.403571            15.360714   

                               goalkeeping_positioning  goalkeeping_reflexes  \
115820.0_one_hot_club_team_id                15.860714             15.596429   

                               goalkeeping_speed   ls   st   rs  lcm   cm  \
115820.0_one_hot_club_team_id           3.1

This works, however i really need to clean up some stuff in the dataset.
1. remove all the one_hot encoded IDs, not needed for the averages of the team members

looking back in the code, i see that up to the "Unique_body_type" one hot encoding there are 128 columns. therefore i want to remove the last 859 columns of the dataset

In [183]:
players_22 = players_22.iloc[: , :-859]

In [184]:
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_contract_valid_until  \
0             72          73.0           1.0                     2023.0   
1             81          21.0           1.0                     2023.0   
2             83          11.0           1.0                     2023.0   
3             68          73.0           1.0                     2025.0   
4             70          10.0           1.0                     2025.0   
...          ...           ...           ...                        ...   
19234         64      112541.0           1.0                     2021.0   
19235         70         445.0           1.0                     2021.0   
19236         72      111131.0           1.0                     2021.0   
19237         66      111131.0           1.0                     2021.0   
19238         61      113040.0           1.0                     2025.0   

       nationality_id     nationality_name  nation_team_id  preferred_foot  \
0                  52            Argentina          1369.0               1   
1                  37               Poland          1353.0              -1   
2                  38             Portugal          1354.0              -1   
3                  54               Brazil            -1.0              -1   
4                   7              Belgium          1325.0              -1   
...               ...                  ...             ...             ...   
19234             155             China PR            -1.0              -1   
19235              25  Republic of Ireland            -1.0              -1   
19236              25  Republic of Ireland            -1.0              -1   
19237              25  Republic of Ireland            -1.0              -1   
19238             159                India            -1.0              -1   

       weak_foot  skill_moves  international_reputation  work_rate  \
0              4            4                         5          3   
1              4            4                         5          8   
2              4            5                         5          5   
3              5            5                         5          8   
4              5            4                         4          9   
...          ...          ...                       ...        ...   
19234          3            2                         1          6   
19235          3            2                         1          6   
19236          3            2                         1          6   
19237          3            2                         1          6   
19238          3            2                         1          6   

       release_clause_eur  pace  shooting  passing  dribbling  defending  \
0             144300000.0  85.0      92.0     91.0       95.0       34.0   
1             197200000.0  78.0      92.0     79.0       86.0       44.0   
2              83300000.0  87.0      94.0     80.0       88.0       34.0   
3             238700000.0  91.0      83.0     86.0       94.0       37.0   

In [185]:
players_22 = players_22.iloc[: , :-2]

In [186]:
players_22

sofifa_id  overall  potential    value_eur  wage_eur  age  height_cm  \
0         158023       93         93   78000000.0  320000.0   34        170   
1         188545       92         92  119500000.0  270000.0   32        185   
2          20801       91         91   45000000.0  270000.0   36        187   
3         190871       91         91  129000000.0  270000.0   29        175   
4         192985       91         91  125500000.0  350000.0   30        181   
...          ...      ...        ...          ...       ...  ...        ...   
19234     261962       47         52      70000.0    1000.0   22        180   
19235     262040       47         59     110000.0     500.0   19        175   
19236     262760       47         55     100000.0     500.0   21        178   
19237     262820       47         60     110000.0     500.0   19        173   
19238     264540       47         60     110000.0     500.0   19        167   

       weight_kg  club_team_id  league_level  club_contract_valid_until  \
0             72          73.0           1.0                     2023.0   
1             81          21.0           1.0                     2023.0   
2             83          11.0           1.0                     2023.0   
3             68          73.0           1.0                     2025.0   
4             70          10.0           1.0                     2025.0   
...          ...           ...           ...                        ...   
19234         64      112541.0           1.0                     2021.0   
19235         70         445.0           1.0                     2021.0   
19236         72      111131.0           1.0                     2021.0   
19237         66      111131.0           1.0                     2021.0   
19238         61      113040.0           1.0                     2025.0   

       nationality_id     nationality_name  nation_team_id  preferred_foot  \
0                  52            Argentina          1369.0               1   
1                  37               Poland          1353.0              -1   
2                  38             Portugal          1354.0              -1   
3                  54               Brazil            -1.0              -1   
4                   7              Belgium          1325.0              -1   
...               ...                  ...             ...             ...   
19234             155             China PR            -1.0              -1   
19235              25  Republic of Ireland            -1.0              -1   
19236              25  Republic of Ireland            -1.0              -1   
19237              25  Republic of Ireland            -1.0              -1   
19238             159                India            -1.0              -1   

       weak_foot  skill_moves  international_reputation  work_rate  \
0              4            4                         5          3   
1              4            4                         5          8   
2              4            5                         5          5   
3              5            5                         5          8   
4              5            4                         4          9   
...          ...          ...                       ...        ...   
19234          3            2                         1          6   
19235          3            2                         1          6   
19236          3            2                         1          6   
19237          3            2                         1          6   
19238          3            2                         1          6   

       release_clause_eur  pace  shooting  passing  dribbling  defending  \
0             144300000.0  85.0      92.0     91.0       95.0       34.0   
1             197200000.0  78.0      92.0     79.0       86.0       44.0   
2              83300000.0  87.0      94.0     80.0       88.0       34.0   
3             238700000.0  91.0      83.0     86.0       94.0       37.0   

In [187]:
mean = players_22[players_22["nationality_name"]=="Uruguay"].mean()
print(mean)
new_df = pd.DataFrame(mean.to_dict(),index=[mean.index.values[12]])
new_df.index = ['Uruguay']
new_df

sofifa_id                     2.384619e+05
overall                       6.727857e+01
potential                     7.158929e+01
value_eur                     3.293286e+06
wage_eur                      8.474286e+03
                                  ...     
Normal (185)_body_type        2.285714e-01
Stocky (170-)_body_type       1.071429e-02
Stocky (170-185)_body_type    5.000000e-02
Stocky (185)_body_type        1.428571e-02
Unique_body_type              1.071429e-02
Length: 107, dtype: float64


C:\Users\Lorand\AppData\Local\Temp\ipykernel_8376\238553332.py:1: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  mean = players_22[players_22["nationality_name"]=="Uruguay"].mean()


sofifa_id    overall  potential     value_eur     wage_eur  \
Uruguay  238461.871429  67.278571  71.589286  3.293286e+06  8474.285714   

               age   height_cm  weight_kg  club_team_id  league_level  \
Uruguay  26.292857  179.846429     74.725     90924.825      1.028571   

         club_contract_valid_until  nationality_id  nation_team_id  \
Uruguay                2022.382143            60.0            -1.0   

         preferred_foot  weak_foot  skill_moves  international_reputation  \
Uruguay       -0.492857   2.796429     2.339286                  1.092857   

         work_rate  release_clause_eur       pace   shooting    passing  \
Uruguay   6.257143        6.593789e+06  66.621726  53.423512  57.541667   

         dribbling  defending  physic  attacking_crossing  \
Uruguay  62.740179  52.055952   64.85           49.185714   

         attacking_finishing  attacking_heading_accuracy  \
Uruguay            47.378571                      54.275   

         attacking_short_passing  attacking_volleys  skill_dribbling  \
Uruguay                60.178571          43.285714             55.7   

         skill_curve  skill_fk_accuracy  skill_long_passing  \
Uruguay    46.610714          44.071429                53.1   

         skill_ball_control  movement_acceleration  movement_sprint_speed  \
Uruguay           60.535714              63.871429              63.135714   

         movement_agility  movement_reactions  movement_balance  \
Uruguay         62.132143           63.567857         63.407143   

         power_shot_power  power_jumping  power_stamina  power_strength  \
Uruguay         57.982143      64.753571         63.625       65.007143   

         power_long_shots  mentality_aggression  mentality_interceptions  \
Uruguay         48.053571             56.871429                48.714286   

         mentality_positioning  mentality_vision  mentality_penalties  \
Uruguay              51.939286         54.196429            49.639286   

         mentality_composure  defending_marking_awareness  \
Uruguay            57.760714                    47.035714   

         defending_standing_tackle  defending_sliding_tackle  \
Uruguay                  48.942857                 46.017857   

         goalkeeping_diving  goalkeeping_handling  goalkeeping_kicking  \
Uruguay           15.496429             15.403571            15.360714   

         goalkeeping_positioning  goalkeeping_reflexes  goalkeeping_speed  \
Uruguay                15.860714             15.596429           3.192857   

          ls   st   rs  lcm   cm  rcm  lwb  rwb   gk  CAM_nation_position  \
Uruguay  inf  inf  inf  inf  inf  inf  inf  inf  inf                  0.0   

         CB_nation_position  CDM_nation_position  CF_nation_position  \
Uruguay                 0.0                  0.0                 0.0   

         CM_nation_position  GK_nation_position  LAM_nation_position  \
Uruguay                 0.0                 0.0                  0.0   

         LB_nation_position  LCB_nation_position  LCM_nation_position  \
Uruguay                 0.0                  0.0                  0.0   

         LDM_nation_position  LF_nation_position  LM_nation_position  \
Uruguay                  0.0                 0.0                 0.0   

         LS_nation_position  LW_nation_position  LWB_nation_position  \
Uruguay                 0.0                 0.0                  0.0   

         RAM_nation_position  RB_nation_position  RCB_nation_position  \
Uruguay                  0.0                 0.0                  0.0   

         RCM_nation_position  RDM_nation_position  RF_nation_position  \
Uruguay                  0.0                  0.0                 0.0   

         RM_nation_position  RS_nation_position  RW_nation_position  \
Uruguay                 0.0                 0.0                 0.0   

         RWB_nation_position  ST_nation_position  SUB_nation_position  \
Uruguay                  0.0                 0.0               

This works for a single country. Now i would like to make it into a for loop to automate this

In [188]:
df = pd.DataFrame(columns=players_22.drop("nationality_name", axis=1).columns)
for team in teams_wo_id:
    
    mean = players_22[players_22["nationality_name"]==team].mean()
    new_df = pd.DataFrame(mean.to_dict(),index=[mean.index.values[-1]])
    df = pd.concat([df, new_df], ignore_index=True)

C:\Users\Lorand\AppData\Local\Temp\ipykernel_8376\2072034085.py:4: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  mean = players_22[players_22["nationality_name"]==team].mean()
C:\Users\Lorand\AppData\Local\Temp\ipykernel_8376\2072034085.py:4: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  mean = players_22[players_22["nationality_name"]==team].mean()
C:\Users\Lorand\AppData\Local\Temp\ipykernel_8376\2072034085.py:4: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  mean = players_22[players

In [189]:
df

sofifa_id    overall  potential       value_eur      wage_eur  \
0   238461.871429  67.278571  71.589286  3293285.714286   8474.285714   
1   238021.266234  69.084416  73.733766  4614707.792208  13317.532468   
2   232758.220472  68.338583  73.086614  4370354.330709   14390.15748   
3             NaN        NaN        NaN             NaN           NaN   
4   227746.166667  65.942708  72.953125  2996145.833333   9719.270833   
5    233401.98374  69.113821  72.918699   4566626.01626  13001.219512   
6   229801.138614  69.485149  73.366337  4820693.069307  12904.455446   
7   240459.831502  64.406593  68.443223  1094337.606838   3626.373626   
8   233708.414062  66.554688  71.585938    2407148.4375      9021.875   
9   247853.129213  64.337079  70.662921  1406348.314607   2813.202247   
10  226352.012308  62.815385  66.692308  1129307.692308   3442.307692   
11  233518.830769  68.246154       73.2  3318692.307692  12713.846154   
12  232427.733333       66.8  71.066667  2041166.666667   8168.333333   
13  237786.228169  59.611268  65.050704   500830.985915   4919.295775   
14  224954.652174  68.652174  70.434783  2105434.782609   11021.73913   
15  235517.952381  69.428571  71.380952  2513571.428571    6190.47619   

          age   height_cm  weight_kg   club_team_id league_level  \
0   26.292857  179.846429     74.725      90924.825     1.028571   
1   25.409091  185.668831  79.155844   34211.941558     1.142857   
2   25.291339  185.031496  76.519685   35450.094488     1.267717   
3         NaN         NaN        NaN            NaN          NaN   
4     24.4375    183.1875  77.838542   18456.911458        1.125   
5   26.349593  186.235772  78.829268   36553.390244     1.113821   
6   26.227723  181.356436  74.861386   38600.970297     1.227723   
7   26.100733   177.40293  71.578755   98757.236264     1.018315   
8      24.625  178.617188  72.453125    47175.28125     1.179688   
9   24.511236  178.247191   72.91573  101300.837079     1.016854   
10      26.92      181.32  74.956923   40023.418462     1.009231   
11  24.815385  182.892308  77.861538   33176.723077     1.430769   
12  25.633333  181.066667  73.933333        30787.9          1.4   
13  25.298592  176.870423  69.850704   98681.704225          1.0   
14  28.043478  178.043478  72.913043   44762.608696          1.0   
15  27.571429  184.619048  78.571429   36346.238095     1.047619   

   club_contract_valid_until nationality_id nation_team_id preferred_foot  \
0                2022.382143           60.0           -1.0      -0.492857   
1                2023.441558           10.0           -1.0      -0.428571   
2                2023.125984          136.0           -1.0      -0.653543   
3                        NaN            NaN            NaN            NaN   
4                2023.026042           47.0           -1.0      -0.572917   
5                2022.845528           51.0           -1.0      -0.495935   
6                     2023.0          129.0           -1.0      -0.445545   
7                2022.384615          163.0           -1.0      -0.641026   
8                2022.828125          117.0           -1.0      -0.515625   
9                2023.398876           57.0           -1.0       -0.52809   
10               2021.892308          167.0           -1.0      -0.643077   
11                    2022.6          103.0           -1.0      -0.507692   
12                    2022.9          145.0           -1.0           -0.2   
13               2023.270423          183.0           -1.0      -0.509859   
14               2022.521739           72.0           -1.0      -0.130435   
15                    2023.0          161.0           -1.0      -0.714286   

   weak_foot skill_moves international_reputation work_rate  \
0   2.796429    2.339286                 1.092857  6.257143   
1   3.090909    2.331169                 1.194805  6.318182   
2   2.944882    2.401575                 1.133858  6.259843   
3        NaN         NaN                      N

In [190]:
teams_wo_id

['Uruguay',
 'Croatia',
 'Senegal',
 'Qatar',
 'Switzerland',
 'Serbia',
 'Morocco',
 'Japan',
 'Ghana',
 'Ecuador',
 'Korea Republic',
 'Cameroon',
 'Tunisia',
 'Saudi Arabia',
 'Costa Rica',
 'IR Iran']

In [191]:
df.index = teams_wo_id

In [192]:
df

sofifa_id    overall  potential       value_eur  \
Uruguay         238461.871429  67.278571  71.589286  3293285.714286   
Croatia         238021.266234  69.084416  73.733766  4614707.792208   
Senegal         232758.220472  68.338583  73.086614  4370354.330709   
Qatar                     NaN        NaN        NaN             NaN   
Switzerland     227746.166667  65.942708  72.953125  2996145.833333   
Serbia           233401.98374  69.113821  72.918699   4566626.01626   
Morocco         229801.138614  69.485149  73.366337  4820693.069307   
Japan           240459.831502  64.406593  68.443223  1094337.606838   
Ghana           233708.414062  66.554688  71.585938    2407148.4375   
Ecuador         247853.129213  64.337079  70.662921  1406348.314607   
Korea Republic  226352.012308  62.815385  66.692308  1129307.692308   
Cameroon        233518.830769  68.246154       73.2  3318692.307692   
Tunisia         232427.733333       66.8  71.066667  2041166.666667   
Saudi Arabia    237786.228169  59.611268  65.050704   500830.985915   
Costa Rica      224954.652174  68.652174  70.434783  2105434.782609   
IR Iran         235517.952381  69.428571  71.380952  2513571.428571   

                    wage_eur        age   height_cm  weight_kg   club_team_id  \
Uruguay          8474.285714  26.292857  179.846429     74.725      90924.825   
Croatia         13317.532468  25.409091  185.668831  79.155844   34211.941558   
Senegal          14390.15748  25.291339  185.031496  76.519685   35450.094488   
Qatar                    NaN        NaN         NaN        NaN            NaN   
Switzerland      9719.270833    24.4375    183.1875  77.838542   18456.911458   
Serbia          13001.219512  26.349593  186.235772  78.829268   36553.390244   
Morocco         12904.455446  26.227723  181.356436  74.861386   38600.970297   
Japan            3626.373626  26.100733   177.40293  71.578755   98757.236264   
Ghana               9021.875     24.625  178.617188  72.453125    47175.28125   
Ecuador          2813.202247  24.511236  178.247191   72.91573  101300.837079   
Korea Republic   3442.307692      26.92      181.32  74.956923   40023.418462   
Cameroon        12713.846154  24.815385  182.892308  77.861538   33176.723077   
Tunisia          8168.333333  25.633333  181.066667  73.933333        30787.9   
Saudi Arabia     4919.295775  25.298592  176.870423  69.850704   98681.704225   
Costa Rica       11021.73913  28.043478  178.043478  72.913043   44762.608696   
IR Iran           6190.47619  27.571429  184.619048  78.571429   36346.238095   

               league_level club_contract_valid_until nationality_id  \
Uruguay            1.028571               2022.382143           60.0   
Croatia            1.142857               2023.441558           10.0   
Senegal            1.267717               2023.125984          136.0   
Qatar                   NaN                       NaN            NaN   
Switzerland           1.125               2023.026042           47.0   
Serbia             1.113821               2022.845528           51.0   
Morocco            1.227723                    2023.0          129.0   
Japan              1.018315               2022.384615          163.0   
Ghana              1.179688               2022.828125          117.0   
Ecuador            1.016854               2023.398876           57.0   
Korea Republic     1.009231               2021.892308          167.0   
Cameroon           1.430769                    2022.6          103.0   
Tunisia                 1.4                    2022.9          145.0   
Saudi Arabia            1.0               2023.270423          183.0   
Costa Rica              1.0               2022.521739           72.0   
IR Iran            1.047619                    2023.0          161.0   

               nation_team_id preferred_foot weak_foot skill_moves  \
Uruguay                  -1.0      -0.492857  2.796429    2.339286   
Croatia                  -1.0      -0.428571  3.090909    2.331169   

In [193]:
columns_to_drop = ["ls","st","rs","lw","lf","cf","rf","rw","lam","cam","ram","lm","lcm","cm","rcm","rm","lwb","ldm","cdm","rdm","rwb","lb","lcb","cb","rcb","rb","gk", "nationality_name"]
df.drop(columns_to_drop, axis=1, inplace=True)

In [194]:
df

sofifa_id    overall  potential       value_eur  \
Uruguay         238461.871429  67.278571  71.589286  3293285.714286   
Croatia         238021.266234  69.084416  73.733766  4614707.792208   
Senegal         232758.220472  68.338583  73.086614  4370354.330709   
Qatar                     NaN        NaN        NaN             NaN   
Switzerland     227746.166667  65.942708  72.953125  2996145.833333   
Serbia           233401.98374  69.113821  72.918699   4566626.01626   
Morocco         229801.138614  69.485149  73.366337  4820693.069307   
Japan           240459.831502  64.406593  68.443223  1094337.606838   
Ghana           233708.414062  66.554688  71.585938    2407148.4375   
Ecuador         247853.129213  64.337079  70.662921  1406348.314607   
Korea Republic  226352.012308  62.815385  66.692308  1129307.692308   
Cameroon        233518.830769  68.246154       73.2  3318692.307692   
Tunisia         232427.733333       66.8  71.066667  2041166.666667   
Saudi Arabia    237786.228169  59.611268  65.050704   500830.985915   
Costa Rica      224954.652174  68.652174  70.434783  2105434.782609   
IR Iran         235517.952381  69.428571  71.380952  2513571.428571   

                    wage_eur        age   height_cm  weight_kg   club_team_id  \
Uruguay          8474.285714  26.292857  179.846429     74.725      90924.825   
Croatia         13317.532468  25.409091  185.668831  79.155844   34211.941558   
Senegal          14390.15748  25.291339  185.031496  76.519685   35450.094488   
Qatar                    NaN        NaN         NaN        NaN            NaN   
Switzerland      9719.270833    24.4375    183.1875  77.838542   18456.911458   
Serbia          13001.219512  26.349593  186.235772  78.829268   36553.390244   
Morocco         12904.455446  26.227723  181.356436  74.861386   38600.970297   
Japan            3626.373626  26.100733   177.40293  71.578755   98757.236264   
Ghana               9021.875     24.625  178.617188  72.453125    47175.28125   
Ecuador          2813.202247  24.511236  178.247191   72.91573  101300.837079   
Korea Republic   3442.307692      26.92      181.32  74.956923   40023.418462   
Cameroon        12713.846154  24.815385  182.892308  77.861538   33176.723077   
Tunisia          8168.333333  25.633333  181.066667  73.933333        30787.9   
Saudi Arabia     4919.295775  25.298592  176.870423  69.850704   98681.704225   
Costa Rica       11021.73913  28.043478  178.043478  72.913043   44762.608696   
IR Iran           6190.47619  27.571429  184.619048  78.571429   36346.238095   

               league_level club_contract_valid_until nationality_id  \
Uruguay            1.028571               2022.382143           60.0   
Croatia            1.142857               2023.441558           10.0   
Senegal            1.267717               2023.125984          136.0   
Qatar                   NaN                       NaN            NaN   
Switzerland           1.125               2023.026042           47.0   
Serbia             1.113821               2022.845528           51.0   
Morocco            1.227723                    2023.0          129.0   
Japan              1.018315               2022.384615          163.0   
Ghana              1.179688               2022.828125          117.0   
Ecuador            1.016854               2023.398876           57.0   
Korea Republic     1.009231               2021.892308          167.0   
Cameroon           1.430769                    2022.6          103.0   
Tunisia                 1.4                    2022.9          145.0   
Saudi Arabia            1.0               2023.270423          183.0   
Costa Rica              1.0               2022.521739           72.0   
IR Iran            1.047619                    2023.0          161.0   

               nation_team_id preferred_foot weak_foot skill_moves  \
Uruguay                  -1.0      -0.492857  2.796429    2.339286   
Croatia                  -1.0      -0.428571  3.090909    2.331169   

In [195]:
last_scores

team        date  rank  goalkeeper_score  defense_score  \
0        Argentina  2022-06-05     4              84.0           82.0   
1        Australia  2022-06-13    42              77.0           72.0   
2          Belgium  2022-06-14     2              89.0           81.0   
3           Brazil  2022-06-06     1              89.0           87.0   
4         Cameroon  2022-06-09    37              67.0           77.0   
5           Canada  2022-06-13    38              76.0           69.0   
6       Costa Rica  2022-06-14    31              88.0           72.0   
7          Croatia  2022-06-13    16              82.0           78.0   
8          Denmark  2022-06-13    11              85.0           80.0   
9          Ecuador  2022-06-11    46              71.0           74.0   
10         England  2022-06-14     5              83.0           85.0   
11          France  2022-06-13     3              87.0           84.0   
12         Germany  2022-06-14    12              88.0           84.0   
13           Ghana  2022-06-14    60              74.0           76.0   
14         IR Iran  2022-06-12    21              73.0           69.0   
15           Japan  2022-06-14    23              73.0           75.0   
16  Korea Republic  2022-06-14    29              75.0           73.0   
17          Mexico  2022-06-14     9              80.0           77.0   
18         Morocco  2022-06-13    24              82.0           81.0   
19     Netherlands  2022-06-14    10              81.0           85.0   
20          Poland  2022-06-14    26              87.0           75.0   
21        Portugal  2022-06-12     8              82.0           85.0   
22           Qatar  2022-03-29    52              50.0           78.0   
23    Saudi Arabia  2022-06-09    49              70.0           73.0   
24         Senegal  2022-06-07    20              83.0           79.0   
25          Serbia  2022-06-12    25              80.0           76.0   
26           Spain  2022-06-12     7              84.0           86.0   
27     Switzerland  2022-06-12    14              85.0           78.0   
28         Tunisia  2022-06-14    35              64.0           71.0   
29             USA  2022-06-14    15              77.0           76.0   
30         Uruguay  2022-06-11    13              80.0           81.0   
31           Wales  2022-06-14    18              74.0           75.0   

    offense_score  midfield_score  
0            89.0            84.0  
1            72.0            74.0  
2            86.0            86.0  
3            87.0            86.0  
4            78.0            75.0  
5            73.0            78.0  
6            70.0            69.0  
7            77.0            84.0  
8            78.0            80.0  
9            76.0            74.0  
10           88.0            84.0  
11           87.0            86.0  
12           83.0            86.0  
13           76.0            78.0  
14           75.0            69.0  
15           75.0            78.0  
16           80.0            74.0  
17           83.0            78.0  
18           82.0            76.0  
19           83.0            84.0  
20           85.0            76.0  
21           86.0            84.0  
22           80.0            79.0  
23           68.0            73.0  
24           81.0            79.0  
25           80.0            82.0  
26           85.0            86.0  
27           77.0            80.0  
28           72.0            74.0  
29           78.0            76.0  
30           84.0            80.0  
31           73.0            78.0

I've successfully gotten the average for 16 of the participating teams. now i need to get them for the rest of the teams players

In [196]:
for i in teams:
    print(i)
    print(players_22[players_22["nationality_name"]==i]["nation_team_id"].unique())

France
[ 1.335e+03 -1.000e+00]
England
[ 1.318e+03 -1.000e+00]
Spain
[ 1.362e+03 -1.000e+00]
Brazil
[-1.00e+00  1.37e+03]
Portugal
[ 1.354e+03 -1.000e+00]
Germany
[ 1.337e+03 -1.000e+00]
Netherlands
[ 1.05035e+05 -1.00000e+00]
Argentina
[ 1.369e+03 -1.000e+00]
Belgium
[ 1.325e+03 -1.000e+00]
Uruguay
[-1.]
Croatia
[-1.]
USA
[ 1.387e+03 -1.000e+00]
Denmark
[ 1.331e+03 -1.000e+00]
Mexico
[-1.000e+00  1.386e+03]
Senegal
[-1.]
Poland
[ 1.353e+03 -1.000e+00]
Qatar
[]
Switzerland
[-1.]
Serbia
[-1.]
Morocco
[-1.]
Japan
[-1.]
Ghana
[-1.]
Wales
[ 1.367e+03 -1.000e+00]
Ecuador
[-1.]
Korea Republic
[-1.]
Cameroon
[-1.]
Canada
[ 1.11455e+05 -1.00000e+00]
Australia
[ 1.415e+03 -1.000e+00]
Tunisia
[-1.]
Saudi Arabia
[-1.]
Costa Rica
[-1.]
IR Iran
[-1.]


In [197]:
teams_w_id = ["Canada", "Australia", "Wales", "Poland", "USA", "Denmark", "Mexico", "France", "England", "Spain", "Brazil", "Portugal", "Germany", "Netherlands", "Argentina", "Belgium"]

I'm running out of time: i want a prediction before the world cup starts if possible. therefore im just going to use what ive already created above. I'm going to forget about team specific players as i feel this would be too much work and would take me too long. It may also be unfair for those teams as they would have less players included in the data

In [198]:
teams_w_id_avg = pd.DataFrame(columns=players_22.drop("nationality_name", axis=1).columns)
for team in teams_w_id:
    
    mean = players_22[players_22["nationality_name"]==team].mean()
    new_df = pd.DataFrame(mean.to_dict(),index=[mean.index.values[-1]])
    teams_w_id_avg = pd.concat([teams_w_id_avg, new_df], ignore_index=True)

teams_w_id_avg.index = teams_w_id
teams_w_id_avg

C:\Users\Lorand\AppData\Local\Temp\ipykernel_8376\4125765300.py:4: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  mean = players_22[players_22["nationality_name"]==team].mean()
C:\Users\Lorand\AppData\Local\Temp\ipykernel_8376\4125765300.py:4: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  mean = players_22[players_22["nationality_name"]==team].mean()
C:\Users\Lorand\AppData\Local\Temp\ipykernel_8376\4125765300.py:4: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  mean = players_22[players

sofifa_id    overall  potential       value_eur  \
Canada       232967.763158  64.052632  70.723684  2418717.105263   
Australia     229330.06015  61.409774  67.718045   781306.390977   
Wales        226616.751825  63.357664  70.379562  1710656.934307   
Poland       232951.863524  63.119107  69.513648  1591389.578164   
USA          235911.353511  63.191283  70.176755   1385835.35109   
Denmark       229449.65798  65.006515  71.026059  2270700.325733   
Mexico       227701.985795  66.068182  71.994318  2287286.931818   
France       232384.453061  67.543878  73.417347  4698387.755102   
England      225303.909831  63.934846  70.728912  2523129.241807   
Spain        228440.590239  69.563536  74.882136  5299113.720074   
Brazil       229967.512821  70.851728  72.971014  5102982.162765   
Portugal     230341.469169  69.726542  75.002681  6086689.008043   
Germany       233604.90939  65.631796  71.305601  2810514.827018   
Netherlands  232897.296128  67.460137  73.958998  4335592.255125   
Argentina    229201.226042  68.721875  73.111458  3268057.291667   
Belgium      227557.831776  67.146417  73.725857  4332819.314642   

                 wage_eur        age   height_cm  weight_kg  club_team_id  \
Canada        5489.473684  24.223684  181.657895      76.25  67196.210526   
Australia     2409.586466   24.43609  181.233083  75.097744  96028.654135   
Wales         9582.481752  24.094891  181.211679  74.160584  12012.467153   
Poland        4814.019851  24.315136  183.332506  75.759305   74669.82134   
USA           4165.496368  24.365617  182.029056  76.782082  57880.653753   
Denmark       8694.136808  24.208469  184.530945  76.954397   8438.120521   
Mexico         10539.0625  25.167614  177.747159    72.6875  61998.599432   
France       13164.387755  24.467347  181.813265  75.060204  25633.768367   
England      10270.418848  24.265852  182.133799  74.223967   13989.01687   
Spain        14599.217311  25.637201  180.507366  73.859116  37767.785451   
Brazil       16266.220736  26.454849  180.663322  75.744705  50617.071349   
Portugal     13966.621984  25.117962  181.123324  74.265416  26314.817694   
Germany       8908.896211  24.543657  183.961285  78.257825  45140.888797   
Netherlands  11534.851936  23.940774  183.437358  75.906606  19903.539863   
Argentina     9265.885417  26.529167  179.035417  74.640625   87469.89375   
Belgium      14490.809969  24.180685  182.311526  75.102804  28228.479751   

            league_level club_contract_valid_until nationality_id  \
Canada          1.151316               2021.914474           70.0   
Australia       1.114662               2022.505639          195.0   
Wales           2.583942               2022.620438           50.0   
Poland          1.110422               2022.923077           37.0   
USA             1.065375               2022.050847           95.0   
Denmark         1.110749                2023.28013           13.0   
Mexico               1.0               2022.784091           83.0   
France          1.440816               2023.121429           18.0   
England          2.55032               2022.677138           14.0   
Spain           1.473297               2022.917127           45.0   
Brazil          1.022297                2023.42252           54.0   
Portugal        1.075067               2023.230563           38.0   
Germany         2.051895               2022.864909           21.0   
Netherlands     1.082005               2023.031891           34.0   
Argentina       1.030208               2022.380208           52.0   
Belgium         1.062305               2023.172897            7.0   

            nation_team_id preferred_foot weak_foot skill_moves  \
Canada        33729.105263      -0.421053  2.802632    2.302632   
Australia        121.43609      -0.526316  2.932331    2.184211   
Wales           228.664234      -0.605839  2.985401    2.248175   
Poland           76.275434      -0.667494  2.709677    2.168734   
USA              76.297821      -0.641646

In [199]:
columns_to_drop = ["ls","st","rs","lw","lf","cf","rf","rw","lam","cam","ram","lm","lcm","cm","rcm","rm","lwb","ldm","cdm","rdm","rwb","lb","lcb","cb","rcb","rb","gk"]
teams_w_id_avg.drop(columns_to_drop, axis=1, inplace=True)

In [200]:
teams_w_id_avg

sofifa_id    overall  potential       value_eur  \
Canada       232967.763158  64.052632  70.723684  2418717.105263   
Australia     229330.06015  61.409774  67.718045   781306.390977   
Wales        226616.751825  63.357664  70.379562  1710656.934307   
Poland       232951.863524  63.119107  69.513648  1591389.578164   
USA          235911.353511  63.191283  70.176755   1385835.35109   
Denmark       229449.65798  65.006515  71.026059  2270700.325733   
Mexico       227701.985795  66.068182  71.994318  2287286.931818   
France       232384.453061  67.543878  73.417347  4698387.755102   
England      225303.909831  63.934846  70.728912  2523129.241807   
Spain        228440.590239  69.563536  74.882136  5299113.720074   
Brazil       229967.512821  70.851728  72.971014  5102982.162765   
Portugal     230341.469169  69.726542  75.002681  6086689.008043   
Germany       233604.90939  65.631796  71.305601  2810514.827018   
Netherlands  232897.296128  67.460137  73.958998  4335592.255125   
Argentina    229201.226042  68.721875  73.111458  3268057.291667   
Belgium      227557.831776  67.146417  73.725857  4332819.314642   

                 wage_eur        age   height_cm  weight_kg  club_team_id  \
Canada        5489.473684  24.223684  181.657895      76.25  67196.210526   
Australia     2409.586466   24.43609  181.233083  75.097744  96028.654135   
Wales         9582.481752  24.094891  181.211679  74.160584  12012.467153   
Poland        4814.019851  24.315136  183.332506  75.759305   74669.82134   
USA           4165.496368  24.365617  182.029056  76.782082  57880.653753   
Denmark       8694.136808  24.208469  184.530945  76.954397   8438.120521   
Mexico         10539.0625  25.167614  177.747159    72.6875  61998.599432   
France       13164.387755  24.467347  181.813265  75.060204  25633.768367   
England      10270.418848  24.265852  182.133799  74.223967   13989.01687   
Spain        14599.217311  25.637201  180.507366  73.859116  37767.785451   
Brazil       16266.220736  26.454849  180.663322  75.744705  50617.071349   
Portugal     13966.621984  25.117962  181.123324  74.265416  26314.817694   
Germany       8908.896211  24.543657  183.961285  78.257825  45140.888797   
Netherlands  11534.851936  23.940774  183.437358  75.906606  19903.539863   
Argentina     9265.885417  26.529167  179.035417  74.640625   87469.89375   
Belgium      14490.809969  24.180685  182.311526  75.102804  28228.479751   

            league_level club_contract_valid_until nationality_id  \
Canada          1.151316               2021.914474           70.0   
Australia       1.114662               2022.505639          195.0   
Wales           2.583942               2022.620438           50.0   
Poland          1.110422               2022.923077           37.0   
USA             1.065375               2022.050847           95.0   
Denmark         1.110749                2023.28013           13.0   
Mexico               1.0               2022.784091           83.0   
France          1.440816               2023.121429           18.0   
England          2.55032               2022.677138           14.0   
Spain           1.473297               2022.917127           45.0   
Brazil          1.022297                2023.42252           54.0   
Portugal        1.075067               2023.230563           38.0   
Germany         2.051895               2022.864909           21.0   
Netherlands     1.082005               2023.031891           34.0   
Argentina       1.030208               2022.380208           52.0   
Belgium         1.062305               2023.172897            7.0   

            nation_team_id preferred_foot weak_foot skill_moves  \
Canada        33729.105263      -0.421053  2.802632    2.302632   
Australia        121.43609      -0.526316  2.932331    2.184211   
Wales           228.664234      -0.605839  2.985401    2.248175   
Poland           76.275434      -0.667494  2.709677    2.168734   
USA              76.297821      -0.641646

In [201]:
last_scores

team        date  rank  goalkeeper_score  defense_score  \
0        Argentina  2022-06-05     4              84.0           82.0   
1        Australia  2022-06-13    42              77.0           72.0   
2          Belgium  2022-06-14     2              89.0           81.0   
3           Brazil  2022-06-06     1              89.0           87.0   
4         Cameroon  2022-06-09    37              67.0           77.0   
5           Canada  2022-06-13    38              76.0           69.0   
6       Costa Rica  2022-06-14    31              88.0           72.0   
7          Croatia  2022-06-13    16              82.0           78.0   
8          Denmark  2022-06-13    11              85.0           80.0   
9          Ecuador  2022-06-11    46              71.0           74.0   
10         England  2022-06-14     5              83.0           85.0   
11          France  2022-06-13     3              87.0           84.0   
12         Germany  2022-06-14    12              88.0           84.0   
13           Ghana  2022-06-14    60              74.0           76.0   
14         IR Iran  2022-06-12    21              73.0           69.0   
15           Japan  2022-06-14    23              73.0           75.0   
16  Korea Republic  2022-06-14    29              75.0           73.0   
17          Mexico  2022-06-14     9              80.0           77.0   
18         Morocco  2022-06-13    24              82.0           81.0   
19     Netherlands  2022-06-14    10              81.0           85.0   
20          Poland  2022-06-14    26              87.0           75.0   
21        Portugal  2022-06-12     8              82.0           85.0   
22           Qatar  2022-03-29    52              50.0           78.0   
23    Saudi Arabia  2022-06-09    49              70.0           73.0   
24         Senegal  2022-06-07    20              83.0           79.0   
25          Serbia  2022-06-12    25              80.0           76.0   
26           Spain  2022-06-12     7              84.0           86.0   
27     Switzerland  2022-06-12    14              85.0           78.0   
28         Tunisia  2022-06-14    35              64.0           71.0   
29             USA  2022-06-14    15              77.0           76.0   
30         Uruguay  2022-06-11    13              80.0           81.0   
31           Wales  2022-06-14    18              74.0           75.0   

    offense_score  midfield_score  
0            89.0            84.0  
1            72.0            74.0  
2            86.0            86.0  
3            87.0            86.0  
4            78.0            75.0  
5            73.0            78.0  
6            70.0            69.0  
7            77.0            84.0  
8            78.0            80.0  
9            76.0            74.0  
10           88.0            84.0  
11           87.0            86.0  
12           83.0            86.0  
13           76.0            78.0  
14           75.0            69.0  
15           75.0            78.0  
16           80.0            74.0  
17           83.0            78.0  
18           82.0            76.0  
19           83.0            84.0  
20           85.0            76.0  
21           86.0            84.0  
22           80.0            79.0  
23           68.0            73.0  
24           81.0            79.0  
25           80.0            82.0  
26           85.0            86.0  
27           77.0            80.0  
28           72.0            74.0  
29           78.0            76.0  
30           84.0            80.0  
31           73.0            78.0

In [202]:
all_teams = pd.concat([teams_w_id_avg, df])



In [203]:

all_teams.index.name = 'team'
all_teams

sofifa_id    overall  potential       value_eur  \
team                                                                  
Canada          232967.763158  64.052632  70.723684  2418717.105263   
Australia        229330.06015  61.409774  67.718045   781306.390977   
Wales           226616.751825  63.357664  70.379562  1710656.934307   
Poland          232951.863524  63.119107  69.513648  1591389.578164   
USA             235911.353511  63.191283  70.176755   1385835.35109   
Denmark          229449.65798  65.006515  71.026059  2270700.325733   
Mexico          227701.985795  66.068182  71.994318  2287286.931818   
France          232384.453061  67.543878  73.417347  4698387.755102   
England         225303.909831  63.934846  70.728912  2523129.241807   
Spain           228440.590239  69.563536  74.882136  5299113.720074   
Brazil          229967.512821  70.851728  72.971014  5102982.162765   
Portugal        230341.469169  69.726542  75.002681  6086689.008043   
Germany          233604.90939  65.631796  71.305601  2810514.827018   
Netherlands     232897.296128  67.460137  73.958998  4335592.255125   
Argentina       229201.226042  68.721875  73.111458  3268057.291667   
Belgium         227557.831776  67.146417  73.725857  4332819.314642   
Uruguay         238461.871429  67.278571  71.589286  3293285.714286   
Croatia         238021.266234  69.084416  73.733766  4614707.792208   
Senegal         232758.220472  68.338583  73.086614  4370354.330709   
Qatar                     NaN        NaN        NaN             NaN   
Switzerland     227746.166667  65.942708  72.953125  2996145.833333   
Serbia           233401.98374  69.113821  72.918699   4566626.01626   
Morocco         229801.138614  69.485149  73.366337  4820693.069307   
Japan           240459.831502  64.406593  68.443223  1094337.606838   
Ghana           233708.414062  66.554688  71.585938    2407148.4375   
Ecuador         247853.129213  64.337079  70.662921  1406348.314607   
Korea Republic  226352.012308  62.815385  66.692308  1129307.692308   
Cameroon        233518.830769  68.246154       73.2  3318692.307692   
Tunisia         232427.733333       66.8  71.066667  2041166.666667   
Saudi Arabia    237786.228169  59.611268  65.050704   500830.985915   
Costa Rica      224954.652174  68.652174  70.434783  2105434.782609   
IR Iran         235517.952381  69.428571  71.380952  2513571.428571   

                    wage_eur        age   height_cm  weight_kg   club_team_id  \
team                                                                            
Canada           5489.473684  24.223684  181.657895      76.25   67196.210526   
Australia        2409.586466   24.43609  181.233083  75.097744   96028.654135   
Wales            9582.481752  24.094891  181.211679  74.160584   12012.467153   
Poland           4814.019851  24.315136  183.332506  75.759305    74669.82134   
USA              4165.496368  24.365617  182.029056  76.782082   57880.653753   
Denmark          8694.136808  24.208469  184.530945  76.954397    8438.120521   
Mexico            10539.0625  25.167614  177.747159    72.6875   61998.599432   
France          13164.387755  24.467347  181.813265  75.060204   25633.768367   
England         10270.418848  24.265852  182.133799  74.223967    13989.01687   
Spain           14599.217311  25.637201  180.507366  73.859116   37767.785451   
Brazil          16266.220736  26.454849  180.663322  75.744705   50617.071349   
Portugal        13966.621984  25.117962  181.123324  74.265416   26314.817694   
Germany          8908.896211  24.543657  183.961285  78.257825   45140.888797   
Netherlands     11534.851936  23.940774  183.437358  75.906606   19903.539863   
Argentina        9265.885417  26.529167  179.035417  74.640625    87469.89375   
Belgium         14490.809969  24.180685  182.311526  75.102804   28228.479751   
Uruguay          8474.285714  26.292857  179.846429     74.725      90924.825   
Croatia         13317.532468  25.409091  185.668831  79.155844   3

In [204]:
last_scores = last_scores.merge(all_teams, on="team")

In [205]:
NAColumns = []
for i in last_scores:
    sum = str(last_scores[i].isna().sum())
    print("N/A: "+ i + " has " + sum)
    if int(sum) != 0:
        NAColumns.append(i)
for i in NAColumns:
    column_average = last_scores[i].mean()
    last_scores[i] = last_scores[i].fillna(column_average)

N/A: team has 0
N/A: date has 0
N/A: rank has 0
N/A: goalkeeper_score has 0
N/A: defense_score has 0
N/A: offense_score has 0
N/A: midfield_score has 0
N/A: sofifa_id has 1
N/A: overall has 1
N/A: potential has 1
N/A: value_eur has 1
N/A: wage_eur has 1
N/A: age has 1
N/A: height_cm has 1
N/A: weight_kg has 1
N/A: club_team_id has 1
N/A: league_level has 1
N/A: club_contract_valid_until has 1
N/A: nationality_id has 1
N/A: nation_team_id has 1
N/A: preferred_foot has 1
N/A: weak_foot has 1
N/A: skill_moves has 1
N/A: international_reputation has 1
N/A: work_rate has 1
N/A: release_clause_eur has 1
N/A: pace has 1
N/A: shooting has 1
N/A: passing has 1
N/A: dribbling has 1
N/A: defending has 1
N/A: physic has 1
N/A: attacking_crossing has 1
N/A: attacking_finishing has 1
N/A: attacking_heading_accuracy has 1
N/A: attacking_short_passing has 1
N/A: attacking_volleys has 1
N/A: skill_dribbling has 1
N/A: skill_curve has 1
N/A: skill_fk_accuracy has 1
N/A: skill_long_passing has 1
N/A: ski

In [206]:
last_scores

team        date  rank  goalkeeper_score  defense_score  \
0        Argentina  2022-06-05     4              84.0           82.0   
1        Australia  2022-06-13    42              77.0           72.0   
2          Belgium  2022-06-14     2              89.0           81.0   
3           Brazil  2022-06-06     1              89.0           87.0   
4         Cameroon  2022-06-09    37              67.0           77.0   
5           Canada  2022-06-13    38              76.0           69.0   
6       Costa Rica  2022-06-14    31              88.0           72.0   
7          Croatia  2022-06-13    16              82.0           78.0   
8          Denmark  2022-06-13    11              85.0           80.0   
9          Ecuador  2022-06-11    46              71.0           74.0   
10         England  2022-06-14     5              83.0           85.0   
11          France  2022-06-13     3              87.0           84.0   
12         Germany  2022-06-14    12              88.0           84.0   
13           Ghana  2022-06-14    60              74.0           76.0   
14         IR Iran  2022-06-12    21              73.0           69.0   
15           Japan  2022-06-14    23              73.0           75.0   
16  Korea Republic  2022-06-14    29              75.0           73.0   
17          Mexico  2022-06-14     9              80.0           77.0   
18         Morocco  2022-06-13    24              82.0           81.0   
19     Netherlands  2022-06-14    10              81.0           85.0   
20          Poland  2022-06-14    26              87.0           75.0   
21        Portugal  2022-06-12     8              82.0           85.0   
22           Qatar  2022-03-29    52              50.0           78.0   
23    Saudi Arabia  2022-06-09    49              70.0           73.0   
24         Senegal  2022-06-07    20              83.0           79.0   
25          Serbia  2022-06-12    25              80.0           76.0   
26           Spain  2022-06-12     7              84.0           86.0   
27     Switzerland  2022-06-12    14              85.0           78.0   
28         Tunisia  2022-06-14    35              64.0           71.0   
29             USA  2022-06-14    15              77.0           76.0   
30         Uruguay  2022-06-11    13              80.0           81.0   
31           Wales  2022-06-14    18              74.0           75.0   

    offense_score  midfield_score      sofifa_id    overall  potential  \
0            89.0            84.0  229201.226042  68.721875  73.111458   
1            72.0            74.0  229330.060150  61.409774  67.718045   
2            86.0            86.0  227557.831776  67.146417  73.725857   
3            87.0            86.0  229967.512821  70.851728  72.971014   
4            78.0            75.0  233518.830769  68.246154  73.200000   
5            73.0            78.0  232967.763158  64.052632  70.723684   
6            70.0            69.0  224954.652174  68.652174  70.434783   
7            77.0            84.0  238021.266234  69.084416  73.733766   
8            78.0            80.0  229449.657980  65.006515  71.026059   
9            76.0            74.0  247853.129213  64.337079  70.662921   
10           88.0            84.0  225303.909831  63.934846  70.728912   
11           87.0            86.0  232384.453061  67.543878  73.417347   
12           83.0            86.0  233604.909390  65.631796  71.305601   
13           76.0            78.0  233708.414062  66.554688  71.585938   
14           75.0            69.0  235517.952381  69.428571  71.380952   
15           75.0            78.0  240459.831502  64.406593  68.443223   
16           80.0            74.0  226352.012308  62.815385  66.692308   
17           83.0            78.0  227701.985795  66.068182  71.994318   
18           82.0            76.0  229801.138614  69.485149  73.366337   
19           83.0            84.0  232897.296128  67.460137  73.958998   
20           85.0            76.0  232951.863524  

In [207]:
last_scores.drop(["sofifa_id", "club_team_id", "nation_team_id"], axis=1,inplace=True)

In [208]:
last_scores

team        date  rank  goalkeeper_score  defense_score  \
0        Argentina  2022-06-05     4              84.0           82.0   
1        Australia  2022-06-13    42              77.0           72.0   
2          Belgium  2022-06-14     2              89.0           81.0   
3           Brazil  2022-06-06     1              89.0           87.0   
4         Cameroon  2022-06-09    37              67.0           77.0   
5           Canada  2022-06-13    38              76.0           69.0   
6       Costa Rica  2022-06-14    31              88.0           72.0   
7          Croatia  2022-06-13    16              82.0           78.0   
8          Denmark  2022-06-13    11              85.0           80.0   
9          Ecuador  2022-06-11    46              71.0           74.0   
10         England  2022-06-14     5              83.0           85.0   
11          France  2022-06-13     3              87.0           84.0   
12         Germany  2022-06-14    12              88.0           84.0   
13           Ghana  2022-06-14    60              74.0           76.0   
14         IR Iran  2022-06-12    21              73.0           69.0   
15           Japan  2022-06-14    23              73.0           75.0   
16  Korea Republic  2022-06-14    29              75.0           73.0   
17          Mexico  2022-06-14     9              80.0           77.0   
18         Morocco  2022-06-13    24              82.0           81.0   
19     Netherlands  2022-06-14    10              81.0           85.0   
20          Poland  2022-06-14    26              87.0           75.0   
21        Portugal  2022-06-12     8              82.0           85.0   
22           Qatar  2022-03-29    52              50.0           78.0   
23    Saudi Arabia  2022-06-09    49              70.0           73.0   
24         Senegal  2022-06-07    20              83.0           79.0   
25          Serbia  2022-06-12    25              80.0           76.0   
26           Spain  2022-06-12     7              84.0           86.0   
27     Switzerland  2022-06-12    14              85.0           78.0   
28         Tunisia  2022-06-14    35              64.0           71.0   
29             USA  2022-06-14    15              77.0           76.0   
30         Uruguay  2022-06-11    13              80.0           81.0   
31           Wales  2022-06-14    18              74.0           75.0   

    offense_score  midfield_score    overall  potential     value_eur  \
0            89.0            84.0  68.721875  73.111458  3.268057e+06   
1            72.0            74.0  61.409774  67.718045  7.813064e+05   
2            86.0            86.0  67.146417  73.725857  4.332819e+06   
3            87.0            86.0  70.851728  72.971014  5.102982e+06   
4            78.0            75.0  68.246154  73.200000  3.318692e+06   
5            73.0            78.0  64.052632  70.723684  2.418717e+06   
6            70.0            69.0  68.652174  70.434783  2.105435e+06   
7            77.0            84.0  69.084416  73.733766  4.614708e+06   
8            78.0            80.0  65.006515  71.026059  2.270700e+06   
9            76.0            74.0  64.337079  70.662921  1.406348e+06   
10           88.0            84.0  63.934846  70.728912  2.523129e+06   
11           87.0            86.0  67.543878  73.417347  4.698388e+06   
12           83.0            86.0  65.631796  71.305601  2.810515e+06   
13           76.0            78.0  66.554688  71.585938  2.407148e+06   
14           75.0            69.0  69.428571  71.380952  2.513571e+06   
15           75.0            78.0  64.406593  68.443223  1.094338e+06   
16           80.0            74.0  62.815385  66.692308  1.129308e+06   
17           83.0            78.0  66.068182  71.994318  2.287287e+06   
18           82.0            76.0  69.485149  73.366337  4.820693e+06   
19           83.0            84.0  67.460137  73.958998  4.335592e+06   
20           85.0            76.0  63.119107  69.513648  1.591390e+06  

## last_scores data cleaning finished!
i just have to remove the date. Last_scores will be used as dictionary of stats for each team

---

---

## setting up int_mat for training

Sources:
1. https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.merge.html
2. https://www.w3schools.com/sql/sql_join_left.asp
3. https://www.w3schools.com/sql/trysql.asp?filename=trysql_select_join_left
4. https://realpython.com/pandas-merge-join-and-concat/
5. https://stackoverflow.com/questions/34049618/how-to-add-a-suffix-or-prefix-to-each-column-name
6. https://www.statology.org/pandas-rename-columns/

In [209]:
int_mat

home_team     away_team  home_team_fifa_rank  away_team_fifa_rank  \
0             Bolivia       Uruguay                   59                   22   
1              Brazil        Mexico                    8                   14   
2             Ecuador     Venezuela                   35                   94   
3              Guinea  Sierra Leone                   65                   86   
4            Paraguay     Argentina                   67                    5   
...               ...           ...                  ...                  ...   
23916         Moldova       Andorra                  180                  153   
23917   Liechtenstein        Latvia                  192                  135   
23918           Chile         Ghana                   28                   60   
23919           Japan       Tunisia                   23                   35   
23920  Korea Republic         Egypt                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  away_team_score                    tournament  \
0                    3                1  FIFA World Cup qualification   
1                    1                1                      Friendly   
2                    5                0  FIFA World Cup qualification   
3                    1                0                      Friendly   
4                    1                3  FIFA World Cup qualification   
...                ...              ...                           ...   
23916                2                1           UEFA Nations League   
23917                0                2           UEFA Nations League   
23918                0                0                     Kirin Cup   
23919                0                3                     Kirin Cup   
23920                4                1                      Friendly   

           city         country  neutral_location  home_team_result  \
0        La Paz         Bolivia                 0                 1   
1        Maceió          Brazil                 0                 0   
2         Quito         Ecuador                 0                 1   
3       Conakry          Guinea                 0                 1   
4      Asunción        Paraguay                 0                -1   
...         ...             ...               ...               ...   
23916  Chișinău         Moldova                 0                 1   
23917     Vaduz   Liechtenstein                 0                -1   
23918     Suita           Japan                 1                -1   
23919     Suita           Japan                 0                -1   
23920     Seoul  Korea Republic                 0                 1   

       home_team_goalkeeper_score  away_team_goalkeeper_score  \
0                       74.963838                   74.212477   
1                       74.963838                   74.212477   
2                       74.963838                   74.212477   
3                       74.963838                   74.212477   
4                       74.963838                   74.212477   
...                           ...                         ...   
23916                   65.000000                

# notes
1. i have to add last_scores into int_mat based on the home_team & away_team: this seems hard to do as if i .merge() based on either column, it might miss out some matches
2. I have to remove the one_hot encoding, then i can do it again

1. the following features are the only not one hot encoded ones:
2. home_team,away_team,home_team_fifa_rank,away_team_fifa_rank,home_team_total_fifa_points,away_team_total_fifa_points,home_team_score, away_team_score,tournament,city,country,neutral_location,home_team_result,home_team_goalkeeper_score,away_team_goalkeeper_score,home_team_mean_defense_score,home_team_mean_offense_score,home_team_mean_midfield_score,away_team_mean_defense_score,away_team_mean_offense_score,away_team_mean_midfield_score,year

22 columns, 456   -   24 = 432

In [210]:
int_mat = int_mat.iloc[: , :-432]
int_mat

home_team     away_team  home_team_fifa_rank  away_team_fifa_rank  \
0             Bolivia       Uruguay                   59                   22   
1              Brazil        Mexico                    8                   14   
2             Ecuador     Venezuela                   35                   94   
3              Guinea  Sierra Leone                   65                   86   
4            Paraguay     Argentina                   67                    5   
...               ...           ...                  ...                  ...   
23916         Moldova       Andorra                  180                  153   
23917   Liechtenstein        Latvia                  192                  135   
23918           Chile         Ghana                   28                   60   
23919           Japan       Tunisia                   23                   35   
23920  Korea Republic         Egypt                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  away_team_score                    tournament  \
0                    3                1  FIFA World Cup qualification   
1                    1                1                      Friendly   
2                    5                0  FIFA World Cup qualification   
3                    1                0                      Friendly   
4                    1                3  FIFA World Cup qualification   
...                ...              ...                           ...   
23916                2                1           UEFA Nations League   
23917                0                2           UEFA Nations League   
23918                0                0                     Kirin Cup   
23919                0                3                     Kirin Cup   
23920                4                1                      Friendly   

           city         country  neutral_location  home_team_result  \
0        La Paz         Bolivia                 0                 1   
1        Maceió          Brazil                 0                 0   
2         Quito         Ecuador                 0                 1   
3       Conakry          Guinea                 0                 1   
4      Asunción        Paraguay                 0                -1   
...         ...             ...               ...               ...   
23916  Chișinău         Moldova                 0                 1   
23917     Vaduz   Liechtenstein                 0                -1   
23918     Suita           Japan                 1                -1   
23919     Suita           Japan                 0                -1   
23920     Seoul  Korea Republic                 0                 1   

       home_team_goalkeeper_score  away_team_goalkeeper_score  \
0                       74.963838                   74.212477   
1                       74.963838                   74.212477   
2                       74.963838                   74.212477   
3                       74.963838                   74.212477   
4                       74.963838                   74.212477   
...                           ...                         ...   
23916                   65.000000                

In [211]:
int_mat = int_mat.iloc[: , :-2]
int_mat

home_team     away_team  home_team_fifa_rank  away_team_fifa_rank  \
0             Bolivia       Uruguay                   59                   22   
1              Brazil        Mexico                    8                   14   
2             Ecuador     Venezuela                   35                   94   
3              Guinea  Sierra Leone                   65                   86   
4            Paraguay     Argentina                   67                    5   
...               ...           ...                  ...                  ...   
23916         Moldova       Andorra                  180                  153   
23917   Liechtenstein        Latvia                  192                  135   
23918           Chile         Ghana                   28                   60   
23919           Japan       Tunisia                   23                   35   
23920  Korea Republic         Egypt                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  away_team_score                    tournament  \
0                    3                1  FIFA World Cup qualification   
1                    1                1                      Friendly   
2                    5                0  FIFA World Cup qualification   
3                    1                0                      Friendly   
4                    1                3  FIFA World Cup qualification   
...                ...              ...                           ...   
23916                2                1           UEFA Nations League   
23917                0                2           UEFA Nations League   
23918                0                0                     Kirin Cup   
23919                0                3                     Kirin Cup   
23920                4                1                      Friendly   

           city         country  neutral_location  home_team_result  \
0        La Paz         Bolivia                 0                 1   
1        Maceió          Brazil                 0                 0   
2         Quito         Ecuador                 0                 1   
3       Conakry          Guinea                 0                 1   
4      Asunción        Paraguay                 0                -1   
...         ...             ...               ...               ...   
23916  Chișinău         Moldova                 0                 1   
23917     Vaduz   Liechtenstein                 0                -1   
23918     Suita           Japan                 1                -1   
23919     Suita           Japan                 0                -1   
23920     Seoul  Korea Republic                 0                 1   

       home_team_goalkeeper_score  away_team_goalkeeper_score  \
0                       74.963838                   74.212477   
1                       74.963838                   74.212477   
2                       74.963838                   74.212477   
3                       74.963838                   74.212477   
4                       74.963838                   74.212477   
...                           ...                         ...   
23916                   65.000000                

In [212]:
last_scores

team        date  rank  goalkeeper_score  defense_score  \
0        Argentina  2022-06-05     4              84.0           82.0   
1        Australia  2022-06-13    42              77.0           72.0   
2          Belgium  2022-06-14     2              89.0           81.0   
3           Brazil  2022-06-06     1              89.0           87.0   
4         Cameroon  2022-06-09    37              67.0           77.0   
5           Canada  2022-06-13    38              76.0           69.0   
6       Costa Rica  2022-06-14    31              88.0           72.0   
7          Croatia  2022-06-13    16              82.0           78.0   
8          Denmark  2022-06-13    11              85.0           80.0   
9          Ecuador  2022-06-11    46              71.0           74.0   
10         England  2022-06-14     5              83.0           85.0   
11          France  2022-06-13     3              87.0           84.0   
12         Germany  2022-06-14    12              88.0           84.0   
13           Ghana  2022-06-14    60              74.0           76.0   
14         IR Iran  2022-06-12    21              73.0           69.0   
15           Japan  2022-06-14    23              73.0           75.0   
16  Korea Republic  2022-06-14    29              75.0           73.0   
17          Mexico  2022-06-14     9              80.0           77.0   
18         Morocco  2022-06-13    24              82.0           81.0   
19     Netherlands  2022-06-14    10              81.0           85.0   
20          Poland  2022-06-14    26              87.0           75.0   
21        Portugal  2022-06-12     8              82.0           85.0   
22           Qatar  2022-03-29    52              50.0           78.0   
23    Saudi Arabia  2022-06-09    49              70.0           73.0   
24         Senegal  2022-06-07    20              83.0           79.0   
25          Serbia  2022-06-12    25              80.0           76.0   
26           Spain  2022-06-12     7              84.0           86.0   
27     Switzerland  2022-06-12    14              85.0           78.0   
28         Tunisia  2022-06-14    35              64.0           71.0   
29             USA  2022-06-14    15              77.0           76.0   
30         Uruguay  2022-06-11    13              80.0           81.0   
31           Wales  2022-06-14    18              74.0           75.0   

    offense_score  midfield_score    overall  potential     value_eur  \
0            89.0            84.0  68.721875  73.111458  3.268057e+06   
1            72.0            74.0  61.409774  67.718045  7.813064e+05   
2            86.0            86.0  67.146417  73.725857  4.332819e+06   
3            87.0            86.0  70.851728  72.971014  5.102982e+06   
4            78.0            75.0  68.246154  73.200000  3.318692e+06   
5            73.0            78.0  64.052632  70.723684  2.418717e+06   
6            70.0            69.0  68.652174  70.434783  2.105435e+06   
7            77.0            84.0  69.084416  73.733766  4.614708e+06   
8            78.0            80.0  65.006515  71.026059  2.270700e+06   
9            76.0            74.0  64.337079  70.662921  1.406348e+06   
10           88.0            84.0  63.934846  70.728912  2.523129e+06   
11           87.0            86.0  67.543878  73.417347  4.698388e+06   
12           83.0            86.0  65.631796  71.305601  2.810515e+06   
13           76.0            78.0  66.554688  71.585938  2.407148e+06   
14           75.0            69.0  69.428571  71.380952  2.513571e+06   
15           75.0            78.0  64.406593  68.443223  1.094338e+06   
16           80.0            74.0  62.815385  66.692308  1.129308e+06   
17           83.0            78.0  66.068182  71.994318  2.287287e+06   
18           82.0            76.0  69.485149  73.366337  4.820693e+06   
19           83.0            84.0  67.460137  73.958998  4.335592e+06   
20           85.0            76.0  63.119107  69.513648  1.591390e+06  

Last thing: fifa scores are missing each team
- https://www.fifa.com/fifa-world-ranking/men?dateId=id13792

I made a word doc with each team and their score:
- 3. Argentina 1773.88
- 38. Australia 1488.72
- 1. Brazil 1841.3
- 2. Belgium 1816.71
- 43. Cameroon 1471.44
- 41. Canada 1475
- 31. Costa Rica 1503.59
- 12. Croatia 1645.64
- 10. Denmark 1666.57
- 44. Ecuador 1464.39
- 5. England 1728.47
- 4. France 1759.78
- 11. Germany 1650.21
- 61. Ghana 1393
- 20. IR Iran 1564.61
- 24. Japan 1559.54
- 28. Korea Republic 1530.3
- 13. Mexico 1644.89
- 22. Morocco 1563.5
- 8. Netherlands 1694.51
- 26. Poland 1548.59
- 9. Portugal 1676.56
- 50. Qatar 1439.89
- 51. Saudi Arabia 1437.78
- 18. Senegal 1584.38
- 21. Serbia 1563.62
- 7. Spain 1715.22
- 15. Switzerland 1635.92
- 30. Tunisia 1507.54
- 16. USA 1627.48
- 14. Uruguay 1638.71
- 19. Wales 1569.82

In [213]:
teams = [[3, "Argentina", 1773.88],
[38, "Australia", 1488.72],
[1, "Brazil", 1841.3],
[2, "Belgium", 1816.71],
[43, "Cameroon", 1471.44],
[41, "Canada", 1475],
[31, "Costa Rica", 1503.59],
[12, "Croatia", 1645.64],
[10, "Denmark", 1666.57],
[44, "Ecuador", 1464.39],
[5, "England", 1728.47],
[4, "France", 1759.78],
[11, "Germany", 1650.21],
[61, "Ghana", 1393],
[20, "IR Iran", 1564.61],
[24, "Japan", 1559.54],
[28, "Korea Republic", 1530.3],
[13, "Mexico", 1644.89],
[22, "Morocco", 1563.5],
[8, "Netherlands", 1694.51],
[26, "Poland", 1548.59],
[9, "Portugal", 1676.56],
[50, "Qatar", 1439.89],
[51, "Saudi Arabia", 1437.78],
[18, "Senegal", 1584.38],
[21, "Serbia", 1563.62],
[7, "Spain", 1715.22],
[15, "Switzerland", 1635.92],
[30, "Tunisia", 1507.54],
[16, "USA", 1627.48],
[14, "Uruguay", 1638.71],
[19, "Wales", 1569.82]]
team_updated_scores = pd.DataFrame(teams, columns=['rank', "team", "team_total_fifa_points"])
team_updated_scores

rank            team  team_total_fifa_points
0      3       Argentina                 1773.88
1     38       Australia                 1488.72
2      1          Brazil                 1841.30
3      2         Belgium                 1816.71
4     43        Cameroon                 1471.44
5     41          Canada                 1475.00
6     31      Costa Rica                 1503.59
7     12         Croatia                 1645.64
8     10         Denmark                 1666.57
9     44         Ecuador                 1464.39
10     5         England                 1728.47
11     4          France                 1759.78
12    11         Germany                 1650.21
13    61           Ghana                 1393.00
14    20         IR Iran                 1564.61
15    24           Japan                 1559.54
16    28  Korea Republic                 1530.30
17    13          Mexico                 1644.89
18    22         Morocco                 1563.50
19     8     Netherlands                 1694.51
20    26          Poland                 1548.59
21     9        Portugal                 1676.56
22    50           Qatar                 1439.89
23    51    Saudi Arabia                 1437.78
24    18         Senegal                 1584.38
25    21          Serbia                 1563.62
26     7           Spain                 1715.22
27    15     Switzerland                 1635.92
28    30         Tunisia                 1507.54
29    16             USA                 1627.48
30    14         Uruguay                 1638.71
31    19           Wales                 1569.82

In [214]:
last_scores.drop("rank", axis=1, inplace=True)

In [215]:
last_scores = last_scores.merge(team_updated_scores, on="team")
last_scores

team        date  goalkeeper_score  defense_score  \
0        Argentina  2022-06-05              84.0           82.0   
1        Australia  2022-06-13              77.0           72.0   
2          Belgium  2022-06-14              89.0           81.0   
3           Brazil  2022-06-06              89.0           87.0   
4         Cameroon  2022-06-09              67.0           77.0   
5           Canada  2022-06-13              76.0           69.0   
6       Costa Rica  2022-06-14              88.0           72.0   
7          Croatia  2022-06-13              82.0           78.0   
8          Denmark  2022-06-13              85.0           80.0   
9          Ecuador  2022-06-11              71.0           74.0   
10         England  2022-06-14              83.0           85.0   
11          France  2022-06-13              87.0           84.0   
12         Germany  2022-06-14              88.0           84.0   
13           Ghana  2022-06-14              74.0           76.0   
14         IR Iran  2022-06-12              73.0           69.0   
15           Japan  2022-06-14              73.0           75.0   
16  Korea Republic  2022-06-14              75.0           73.0   
17          Mexico  2022-06-14              80.0           77.0   
18         Morocco  2022-06-13              82.0           81.0   
19     Netherlands  2022-06-14              81.0           85.0   
20          Poland  2022-06-14              87.0           75.0   
21        Portugal  2022-06-12              82.0           85.0   
22           Qatar  2022-03-29              50.0           78.0   
23    Saudi Arabia  2022-06-09              70.0           73.0   
24         Senegal  2022-06-07              83.0           79.0   
25          Serbia  2022-06-12              80.0           76.0   
26           Spain  2022-06-12              84.0           86.0   
27     Switzerland  2022-06-12              85.0           78.0   
28         Tunisia  2022-06-14              64.0           71.0   
29             USA  2022-06-14              77.0           76.0   
30         Uruguay  2022-06-11              80.0           81.0   
31           Wales  2022-06-14              74.0           75.0   

    offense_score  midfield_score    overall  potential     value_eur  \
0            89.0            84.0  68.721875  73.111458  3.268057e+06   
1            72.0            74.0  61.409774  67.718045  7.813064e+05   
2            86.0            86.0  67.146417  73.725857  4.332819e+06   
3            87.0            86.0  70.851728  72.971014  5.102982e+06   
4            78.0            75.0  68.246154  73.200000  3.318692e+06   
5            73.0            78.0  64.052632  70.723684  2.418717e+06   
6            70.0            69.0  68.652174  70.434783  2.105435e+06   
7            77.0            84.0  69.084416  73.733766  4.614708e+06   
8            78.0            80.0  65.006515  71.026059  2.270700e+06   
9            76.0            74.0  64.337079  70.662921  1.406348e+06   
10           88.0            84.0  63.934846  70.728912  2.523129e+06   
11           87.0            86.0  67.543878  73.417347  4.698388e+06   
12           83.0            86.0  65.631796  71.305601  2.810515e+06   
13           76.0            78.0  66.554688  71.585938  2.407148e+06   
14           75.0            69.0  69.428571  71.380952  2.513571e+06   
15           75.0            78.0  64.406593  68.443223  1.094338e+06   
16           80.0            74.0  62.815385  66.692308  1.129308e+06   
17           83.0            78.0  66.068182  71.994318  2.287287e+06   
18           82.0            76.0  69.485149  73.366337  4.820693e+06   
19           83.0            84.0  67.460137  73.958998  4.335592e+06   
20           85.0            76.0  63.119107  69.513648  1.591390e+06   
21           86.0            84.0  69.726542  75.002681  6.086689e+06   
22           80.0            79.0  66.351002  71.509723  2.970382e+06   
23           68.0            73.0  59.611268  65.0

In [216]:
last_scores

team        date  goalkeeper_score  defense_score  \
0        Argentina  2022-06-05              84.0           82.0   
1        Australia  2022-06-13              77.0           72.0   
2          Belgium  2022-06-14              89.0           81.0   
3           Brazil  2022-06-06              89.0           87.0   
4         Cameroon  2022-06-09              67.0           77.0   
5           Canada  2022-06-13              76.0           69.0   
6       Costa Rica  2022-06-14              88.0           72.0   
7          Croatia  2022-06-13              82.0           78.0   
8          Denmark  2022-06-13              85.0           80.0   
9          Ecuador  2022-06-11              71.0           74.0   
10         England  2022-06-14              83.0           85.0   
11          France  2022-06-13              87.0           84.0   
12         Germany  2022-06-14              88.0           84.0   
13           Ghana  2022-06-14              74.0           76.0   
14         IR Iran  2022-06-12              73.0           69.0   
15           Japan  2022-06-14              73.0           75.0   
16  Korea Republic  2022-06-14              75.0           73.0   
17          Mexico  2022-06-14              80.0           77.0   
18         Morocco  2022-06-13              82.0           81.0   
19     Netherlands  2022-06-14              81.0           85.0   
20          Poland  2022-06-14              87.0           75.0   
21        Portugal  2022-06-12              82.0           85.0   
22           Qatar  2022-03-29              50.0           78.0   
23    Saudi Arabia  2022-06-09              70.0           73.0   
24         Senegal  2022-06-07              83.0           79.0   
25          Serbia  2022-06-12              80.0           76.0   
26           Spain  2022-06-12              84.0           86.0   
27     Switzerland  2022-06-12              85.0           78.0   
28         Tunisia  2022-06-14              64.0           71.0   
29             USA  2022-06-14              77.0           76.0   
30         Uruguay  2022-06-11              80.0           81.0   
31           Wales  2022-06-14              74.0           75.0   

    offense_score  midfield_score    overall  potential     value_eur  \
0            89.0            84.0  68.721875  73.111458  3.268057e+06   
1            72.0            74.0  61.409774  67.718045  7.813064e+05   
2            86.0            86.0  67.146417  73.725857  4.332819e+06   
3            87.0            86.0  70.851728  72.971014  5.102982e+06   
4            78.0            75.0  68.246154  73.200000  3.318692e+06   
5            73.0            78.0  64.052632  70.723684  2.418717e+06   
6            70.0            69.0  68.652174  70.434783  2.105435e+06   
7            77.0            84.0  69.084416  73.733766  4.614708e+06   
8            78.0            80.0  65.006515  71.026059  2.270700e+06   
9            76.0            74.0  64.337079  70.662921  1.406348e+06   
10           88.0            84.0  63.934846  70.728912  2.523129e+06   
11           87.0            86.0  67.543878  73.417347  4.698388e+06   
12           83.0            86.0  65.631796  71.305601  2.810515e+06   
13           76.0            78.0  66.554688  71.585938  2.407148e+06   
14           75.0            69.0  69.428571  71.380952  2.513571e+06   
15           75.0            78.0  64.406593  68.443223  1.094338e+06   
16           80.0            74.0  62.815385  66.692308  1.129308e+06   
17           83.0            78.0  66.068182  71.994318  2.287287e+06   
18           82.0            76.0  69.485149  73.366337  4.820693e+06   
19           83.0            84.0  67.460137  73.958998  4.335592e+06   
20           85.0            76.0  63.119107  69.513648  1.591390e+06   
21           86.0            84.0  69.726542  75.002681  6.086689e+06   
22           80.0            79.0  66.351002  71.509723  2.970382e+06   
23           68.0            73.0  59.611268  65.0

In [217]:
last_scores.columns = last_scores.columns.str.replace('rank_x', 'rank')
last_scores.columns = last_scores.columns.str.replace('team_total_fifa_points_x', 'team_total_fifa_points')


last_scores

team        date  goalkeeper_score  defense_score  \
0        Argentina  2022-06-05              84.0           82.0   
1        Australia  2022-06-13              77.0           72.0   
2          Belgium  2022-06-14              89.0           81.0   
3           Brazil  2022-06-06              89.0           87.0   
4         Cameroon  2022-06-09              67.0           77.0   
5           Canada  2022-06-13              76.0           69.0   
6       Costa Rica  2022-06-14              88.0           72.0   
7          Croatia  2022-06-13              82.0           78.0   
8          Denmark  2022-06-13              85.0           80.0   
9          Ecuador  2022-06-11              71.0           74.0   
10         England  2022-06-14              83.0           85.0   
11          France  2022-06-13              87.0           84.0   
12         Germany  2022-06-14              88.0           84.0   
13           Ghana  2022-06-14              74.0           76.0   
14         IR Iran  2022-06-12              73.0           69.0   
15           Japan  2022-06-14              73.0           75.0   
16  Korea Republic  2022-06-14              75.0           73.0   
17          Mexico  2022-06-14              80.0           77.0   
18         Morocco  2022-06-13              82.0           81.0   
19     Netherlands  2022-06-14              81.0           85.0   
20          Poland  2022-06-14              87.0           75.0   
21        Portugal  2022-06-12              82.0           85.0   
22           Qatar  2022-03-29              50.0           78.0   
23    Saudi Arabia  2022-06-09              70.0           73.0   
24         Senegal  2022-06-07              83.0           79.0   
25          Serbia  2022-06-12              80.0           76.0   
26           Spain  2022-06-12              84.0           86.0   
27     Switzerland  2022-06-12              85.0           78.0   
28         Tunisia  2022-06-14              64.0           71.0   
29             USA  2022-06-14              77.0           76.0   
30         Uruguay  2022-06-11              80.0           81.0   
31           Wales  2022-06-14              74.0           75.0   

    offense_score  midfield_score    overall  potential     value_eur  \
0            89.0            84.0  68.721875  73.111458  3.268057e+06   
1            72.0            74.0  61.409774  67.718045  7.813064e+05   
2            86.0            86.0  67.146417  73.725857  4.332819e+06   
3            87.0            86.0  70.851728  72.971014  5.102982e+06   
4            78.0            75.0  68.246154  73.200000  3.318692e+06   
5            73.0            78.0  64.052632  70.723684  2.418717e+06   
6            70.0            69.0  68.652174  70.434783  2.105435e+06   
7            77.0            84.0  69.084416  73.733766  4.614708e+06   
8            78.0            80.0  65.006515  71.026059  2.270700e+06   
9            76.0            74.0  64.337079  70.662921  1.406348e+06   
10           88.0            84.0  63.934846  70.728912  2.523129e+06   
11           87.0            86.0  67.543878  73.417347  4.698388e+06   
12           83.0            86.0  65.631796  71.305601  2.810515e+06   
13           76.0            78.0  66.554688  71.585938  2.407148e+06   
14           75.0            69.0  69.428571  71.380952  2.513571e+06   
15           75.0            78.0  64.406593  68.443223  1.094338e+06   
16           80.0            74.0  62.815385  66.692308  1.129308e+06   
17           83.0            78.0  66.068182  71.994318  2.287287e+06   
18           82.0            76.0  69.485149  73.366337  4.820693e+06   
19           83.0            84.0  67.460137  73.958998  4.335592e+06   
20           85.0            76.0  63.119107  69.513648  1.591390e+06   
21           86.0            84.0  69.726542  75.002681  6.086689e+06   
22           80.0            79.0  66.351002  71.509723  2.970382e+06   
23           68.0            73.0  59.611268  65.0

In [218]:
last_scores_home = last_scores.add_suffix('_home')
last_scores_away = last_scores.add_suffix('_away')
last_scores_away.columns = last_scores_away.columns.str.replace('team_away', 'away_team')
last_scores_home.columns = last_scores_home.columns.str.replace('team_home', 'home_team')

In [219]:
last_scores_away

away_team   date_away  goalkeeper_score_away  defense_score_away  \
0        Argentina  2022-06-05                   84.0                82.0   
1        Australia  2022-06-13                   77.0                72.0   
2          Belgium  2022-06-14                   89.0                81.0   
3           Brazil  2022-06-06                   89.0                87.0   
4         Cameroon  2022-06-09                   67.0                77.0   
5           Canada  2022-06-13                   76.0                69.0   
6       Costa Rica  2022-06-14                   88.0                72.0   
7          Croatia  2022-06-13                   82.0                78.0   
8          Denmark  2022-06-13                   85.0                80.0   
9          Ecuador  2022-06-11                   71.0                74.0   
10         England  2022-06-14                   83.0                85.0   
11          France  2022-06-13                   87.0                84.0   
12         Germany  2022-06-14                   88.0                84.0   
13           Ghana  2022-06-14                   74.0                76.0   
14         IR Iran  2022-06-12                   73.0                69.0   
15           Japan  2022-06-14                   73.0                75.0   
16  Korea Republic  2022-06-14                   75.0                73.0   
17          Mexico  2022-06-14                   80.0                77.0   
18         Morocco  2022-06-13                   82.0                81.0   
19     Netherlands  2022-06-14                   81.0                85.0   
20          Poland  2022-06-14                   87.0                75.0   
21        Portugal  2022-06-12                   82.0                85.0   
22           Qatar  2022-03-29                   50.0                78.0   
23    Saudi Arabia  2022-06-09                   70.0                73.0   
24         Senegal  2022-06-07                   83.0                79.0   
25          Serbia  2022-06-12                   80.0                76.0   
26           Spain  2022-06-12                   84.0                86.0   
27     Switzerland  2022-06-12                   85.0                78.0   
28         Tunisia  2022-06-14                   64.0                71.0   
29             USA  2022-06-14                   77.0                76.0   
30         Uruguay  2022-06-11                   80.0                81.0   
31           Wales  2022-06-14                   74.0                75.0   

    offense_score_away  midfield_score_away  overall_away  potential_away  \
0                 89.0                 84.0     68.721875       73.111458   
1                 72.0                 74.0     61.409774       67.718045   
2                 86.0                 86.0     67.146417       73.725857   
3                 87.0                 86.0     70.851728       72.971014   
4                 78.0                 75.0     68.246154       73.200000   
5                 73.0                 78.0     64.052632       70.723684   
6                 70.0                 69.0     68.652174       70.434783   
7                 77.0                 84.0     69.084416       73.733766   
8                 78.0                 80.0     65.006515       71.026059   
9                 76.0                 74.0     64.337079       70.662921   
10                88.0                 84.0     63.934846       70.728912   
11                87.0                 86.0     67.543878       73.417347   
12                83.0                 86.0     65.631796       71.305601   
13                76.0                 78.0     66.554688       71.585938   
14                75.0                 69.0     69.428571       71.380952   
15                75.0                 78.0     64.406593       68.443223   
16                80.0                 74.0     62.815385       66.692308   
17                83.0                 78.0     66.068182       71.994318   
18  

In [220]:
#21/11/2022 a major issue happened here: the commented code adds an _x onto the column names, which later messes up my prediction due to mismatching datasets

#int_mat = int_mat.merge(last_scores_home, how="left", on="home_team")
#int_mat = int_mat.merge(last_scores_away, how="left", on="away_team")

int_mat = int_mat.merge(last_scores_home, how="left", on="home_team") #this on its own does not add an X
int_mat = int_mat.merge(last_scores_away, how="left", on="away_team")
int_mat

home_team     away_team  home_team_fifa_rank  away_team_fifa_rank  \
0             Bolivia       Uruguay                   59                   22   
1              Brazil        Mexico                    8                   14   
2             Ecuador     Venezuela                   35                   94   
3              Guinea  Sierra Leone                   65                   86   
4            Paraguay     Argentina                   67                    5   
...               ...           ...                  ...                  ...   
23916         Moldova       Andorra                  180                  153   
23917   Liechtenstein        Latvia                  192                  135   
23918           Chile         Ghana                   28                   60   
23919           Japan       Tunisia                   23                   35   
23920  Korea Republic         Egypt                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  away_team_score                    tournament  \
0                    3                1  FIFA World Cup qualification   
1                    1                1                      Friendly   
2                    5                0  FIFA World Cup qualification   
3                    1                0                      Friendly   
4                    1                3  FIFA World Cup qualification   
...                ...              ...                           ...   
23916                2                1           UEFA Nations League   
23917                0                2           UEFA Nations League   
23918                0                0                     Kirin Cup   
23919                0                3                     Kirin Cup   
23920                4                1                      Friendly   

           city         country  neutral_location  home_team_result  \
0        La Paz         Bolivia                 0                 1   
1        Maceió          Brazil                 0                 0   
2         Quito         Ecuador                 0                 1   
3       Conakry          Guinea                 0                 1   
4      Asunción        Paraguay                 0                -1   
...         ...             ...               ...               ...   
23916  Chișinău         Moldova                 0                 1   
23917     Vaduz   Liechtenstein                 0                -1   
23918     Suita           Japan                 1                -1   
23919     Suita           Japan                 0                -1   
23920     Seoul  Korea Republic                 0                 1   

       home_team_goalkeeper_score  away_team_goalkeeper_score  \
0                       74.963838                   74.212477   
1                       74.963838                   74.212477   
2                       74.963838                   74.212477   
3                       74.963838                   74.212477   
4                       74.963838                   74.212477   
...                           ...                         ...   
23916                   65.000000                

In [221]:
int_mat.drop(["date_home", "date_away"], axis=1, inplace=True)

In [222]:
int_mat

home_team     away_team  home_team_fifa_rank  away_team_fifa_rank  \
0             Bolivia       Uruguay                   59                   22   
1              Brazil        Mexico                    8                   14   
2             Ecuador     Venezuela                   35                   94   
3              Guinea  Sierra Leone                   65                   86   
4            Paraguay     Argentina                   67                    5   
...               ...           ...                  ...                  ...   
23916         Moldova       Andorra                  180                  153   
23917   Liechtenstein        Latvia                  192                  135   
23918           Chile         Ghana                   28                   60   
23919           Japan       Tunisia                   23                   35   
23920  Korea Republic         Egypt                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  away_team_score                    tournament  \
0                    3                1  FIFA World Cup qualification   
1                    1                1                      Friendly   
2                    5                0  FIFA World Cup qualification   
3                    1                0                      Friendly   
4                    1                3  FIFA World Cup qualification   
...                ...              ...                           ...   
23916                2                1           UEFA Nations League   
23917                0                2           UEFA Nations League   
23918                0                0                     Kirin Cup   
23919                0                3                     Kirin Cup   
23920                4                1                      Friendly   

           city         country  neutral_location  home_team_result  \
0        La Paz         Bolivia                 0                 1   
1        Maceió          Brazil                 0                 0   
2         Quito         Ecuador                 0                 1   
3       Conakry          Guinea                 0                 1   
4      Asunción        Paraguay                 0                -1   
...         ...             ...               ...               ...   
23916  Chișinău         Moldova                 0                 1   
23917     Vaduz   Liechtenstein                 0                -1   
23918     Suita           Japan                 1                -1   
23919     Suita           Japan                 0                -1   
23920     Seoul  Korea Republic                 0                 1   

       home_team_goalkeeper_score  away_team_goalkeeper_score  \
0                       74.963838                   74.212477   
1                       74.963838                   74.212477   
2                       74.963838                   74.212477   
3                       74.963838                   74.212477   
4                       74.963838                   74.212477   
...                           ...                         ...   
23916                   65.000000                

In [223]:
NAColumns = []
for i in int_mat:
    sum = str(int_mat[i].isna().sum())
    print("N/A: "+ i + " has " + sum)
    if int(sum) != 0:
        NAColumns.append(i)
for i in NAColumns:
    column_average = int_mat[i].mean()
    int_mat[i] = int_mat[i].fillna(column_average)

N/A: home_team has 0
N/A: away_team has 0
N/A: home_team_fifa_rank has 0
N/A: away_team_fifa_rank has 0
N/A: home_team_total_fifa_points has 0
N/A: away_team_total_fifa_points has 0
N/A: home_team_score has 0
N/A: away_team_score has 0
N/A: tournament has 0
N/A: city has 0
N/A: country has 0
N/A: neutral_location has 0
N/A: home_team_result has 0
N/A: home_team_goalkeeper_score has 0
N/A: away_team_goalkeeper_score has 0
N/A: home_team_mean_defense_score has 0
N/A: home_team_mean_offense_score has 0
N/A: home_team_mean_midfield_score has 0
N/A: away_team_mean_defense_score has 0
N/A: away_team_mean_offense_score has 0
N/A: away_team_mean_midfield_score has 0
N/A: year has 0
N/A: goalkeeper_score_home has 17826
N/A: defense_score_home has 17826
N/A: offense_score_home has 17826
N/A: midfield_score_home has 17826
N/A: overall_home has 17826
N/A: potential_home has 17826
N/A: value_eur_home has 17826
N/A: wage_eur_home has 17826
N/A: age_home has 17826
N/A: height_cm_home has 17826
N/A: w

In [224]:
int_mat

home_team     away_team  home_team_fifa_rank  away_team_fifa_rank  \
0             Bolivia       Uruguay                   59                   22   
1              Brazil        Mexico                    8                   14   
2             Ecuador     Venezuela                   35                   94   
3              Guinea  Sierra Leone                   65                   86   
4            Paraguay     Argentina                   67                    5   
...               ...           ...                  ...                  ...   
23916         Moldova       Andorra                  180                  153   
23917   Liechtenstein        Latvia                  192                  135   
23918           Chile         Ghana                   28                   60   
23919           Japan       Tunisia                   23                   35   
23920  Korea Republic         Egypt                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       home_team_score  away_team_score                    tournament  \
0                    3                1  FIFA World Cup qualification   
1                    1                1                      Friendly   
2                    5                0  FIFA World Cup qualification   
3                    1                0                      Friendly   
4                    1                3  FIFA World Cup qualification   
...                ...              ...                           ...   
23916                2                1           UEFA Nations League   
23917                0                2           UEFA Nations League   
23918                0                0                     Kirin Cup   
23919                0                3                     Kirin Cup   
23920                4                1                      Friendly   

           city         country  neutral_location  home_team_result  \
0        La Paz         Bolivia                 0                 1   
1        Maceió          Brazil                 0                 0   
2         Quito         Ecuador                 0                 1   
3       Conakry          Guinea                 0                 1   
4      Asunción        Paraguay                 0                -1   
...         ...             ...               ...               ...   
23916  Chișinău         Moldova                 0                 1   
23917     Vaduz   Liechtenstein                 0                -1   
23918     Suita           Japan                 1                -1   
23919     Suita           Japan                 0                -1   
23920     Seoul  Korea Republic                 0                 1   

       home_team_goalkeeper_score  away_team_goalkeeper_score  \
0                       74.963838                   74.212477   
1                       74.963838                   74.212477   
2                       74.963838                   74.212477   
3                       74.963838                   74.212477   
4                       74.963838                   74.212477   
...                           ...                         ...   
23916                   65.000000                

In [225]:
int_mat.drop(["tournament", "city", "country", "home_team_score", "away_team_score"], axis=1, inplace=True)
int_mat

home_team     away_team  home_team_fifa_rank  away_team_fifa_rank  \
0             Bolivia       Uruguay                   59                   22   
1              Brazil        Mexico                    8                   14   
2             Ecuador     Venezuela                   35                   94   
3              Guinea  Sierra Leone                   65                   86   
4            Paraguay     Argentina                   67                    5   
...               ...           ...                  ...                  ...   
23916         Moldova       Andorra                  180                  153   
23917   Liechtenstein        Latvia                  192                  135   
23918           Chile         Ghana                   28                   60   
23919           Japan       Tunisia                   23                   35   
23920  Korea Republic         Egypt                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       neutral_location  home_team_result  home_team_goalkeeper_score  \
0                     0                 1                   74.963838   
1                     0                 0                   74.963838   
2                     0                 1                   74.963838   
3                     0                 1                   74.963838   
4                     0                -1                   74.963838   
...                 ...               ...                         ...   
23916                 0                 1                   65.000000   
23917                 0                -1                   74.963838   
23918                 1                -1                   79.000000   
23919                 0                -1                   73.000000   
23920                 0                 1                   75.000000   

       away_team_goalkeeper_score  home_team_mean_defense_score  \
0                       74.212477                     74.903249   
1                       74.212477                     74.903249   
2                       74.212477                     74.903249   
3                       74.212477                     74.903249   
4                       74.212477                     74.903249   
...                           ...                           ...   
23916                   74.212477                     74.903249   
23917                   65.000000                     74.903249   
23918                   74.000000                     75.500000   
23919                   74.212477                     75.200000   
23920                   74.212477                     73.000000   

       home_team_mean_offense_score  home_team_mean_midfield_score  \
0                         75.818743                      75.889292   
1                         75.818743                      75.889292   
2                         75.818743                      75.889292   
3                         75.818743                      75.889292   
4                         75.818743                      75.889292   
...                             ...                            ...   
23916                     75.818743                      75.88

now i need to one hot encode the team names, and the data is ready to start training a model on it!

In [226]:
#time to one-hot encode!
one_hot_home_team = pd.get_dummies(int_mat['home_team'])
one_hot_away_team = pd.get_dummies(int_mat['away_team'])

one_hot_home_team.columns = [str(col) + '_home_team' for col in one_hot_home_team.columns]
one_hot_away_team.columns = [str(col) + '_away_team' for col in one_hot_away_team.columns]
int_mat = pd.concat([int_mat, one_hot_home_team,  one_hot_away_team], axis=1, join="inner")


In [228]:
int_mat

home_team     away_team  home_team_fifa_rank  away_team_fifa_rank  \
0             Bolivia       Uruguay                   59                   22   
1              Brazil        Mexico                    8                   14   
2             Ecuador     Venezuela                   35                   94   
3              Guinea  Sierra Leone                   65                   86   
4            Paraguay     Argentina                   67                    5   
...               ...           ...                  ...                  ...   
23916         Moldova       Andorra                  180                  153   
23917   Liechtenstein        Latvia                  192                  135   
23918           Chile         Ghana                   28                   60   
23919           Japan       Tunisia                   23                   35   
23920  Korea Republic         Egypt                   29                   32   

       home_team_total_fifa_points  away_team_total_fifa_points  \
0                                0                            0   
1                                0                            0   
2                                0                            0   
3                                0                            0   
4                                0                            0   
...                            ...                          ...   
23916                          932                         1040   
23917                          895                         1105   
23918                         1526                         1387   
23919                         1553                         1499   
23920                         1519                         1500   

       neutral_location  home_team_result  home_team_goalkeeper_score  \
0                     0                 1                   74.963838   
1                     0                 0                   74.963838   
2                     0                 1                   74.963838   
3                     0                 1                   74.963838   
4                     0                -1                   74.963838   
...                 ...               ...                         ...   
23916                 0                 1                   65.000000   
23917                 0                -1                   74.963838   
23918                 1                -1                   79.000000   
23919                 0                -1                   73.000000   
23920                 0                 1                   75.000000   

       away_team_goalkeeper_score  home_team_mean_defense_score  \
0                       74.212477                     74.903249   
1                       74.212477                     74.903249   
2                       74.212477                     74.903249   
3                       74.212477                     74.903249   
4                       74.212477                     74.903249   
...                           ...                           ...   
23916                   74.212477                     74.903249   
23917                   65.000000                     74.903249   
23918                   74.000000                     75.500000   
23919                   74.212477                     75.200000   
23920                   74.212477                     73.000000   

       home_team_mean_offense_score  home_team_mean_midfield_score  \
0                         75.818743                      75.889292   
1                         75.818743                      75.889292   
2                         75.818743                      75.889292   
3                         75.818743                      75.889292   
4                         75.818743                      75.889292   
...                             ...                            ...   
23916                     75.818743                      75.88

Exporting data

In [227]:
int_mat.to_csv('int_mat_updated.csv')
last_scores.to_csv('last_scores_updated.csv')

## Done, time to predict!

*here i moved to "World Cup - 2022 Qatar Model Testing.ipynb"*